# PySpark - Fundamentos e aplicações

A ideia deste *notebook* é apresentar os fundamentos de uso da API *Python* para *Spark*. Vamos verificar os principais comandos, e entender o que são ações, transformações, execução *lazy* e as famosas DAG's geradas pelo *Spark* (essa última parte de uma forma mais superficial).

Tudo isso será feito dentro de um ambiente *Databricks*, o qual conta com algumas funcionalidades que facilitam nosso trabalho diário.

Após essa breve introdução e explanação dos conceitos, nós iremos simular uma utilização em um problema de negócio, para facilitar a assimilação de tudo que foi visto.

## Pontos importantes sobre essa interface

A aba na lateral direita nos permite:

- criar *notebooks*, a partir da opção *create*;
- importar dados, também na opção *create*. Essa importação é feita a partir de uma interface gráfica, muito simples de ser utilizada (vale a pena o teste);
- criação de um *cluster* na opção *compute*. Todo *notebook* deve ser associado a um *cluster* para execução.

## Dados utilizados

Os dados utilizados estão dispobilizados no *Kaggle*:

- Link para *download*: [Conjunto de dados](https://www.kaggle.com/olistbr/brazilian-ecommerce?select=olist_order_payments_dataset.csv)

Nesse projeto vamos utilizar as tabelas:

- *olist_customers_dataset.csv*;
- *olist_order_payments_dataset.csv*;
- *olist_orders_dataset.csv*.

### Contexto dos dados

"*This dataset was generously provided by Olist, the largest department store in Brazilian marketplaces. Olist connects small businesses from all over Brazil to channels without hassle and with a single contract. Those merchants are able to sell their products through the Olist Store and ship them directly to the customers using Olist logistics partners. After a customer purchases the product from Olist Store a seller gets notified to fulfill that order. Once the customer receives the product, or the estimated delivery date is due, the customer gets a satisfaction survey by email where he can give a note for the purchase experience and write down some comments.*"

#### Link entre os dados

![databases](https://i.imgur.com/HRhd2Y0.png)

## Referências úteis

- Documentação: [Documentação PySpark](https://spark.apache.org/docs/latest/api/python/index.html);
- Criando tabelas: [Criação de tabelas no databricks](https://docs.databricks.com/data/tables.html).

In [0]:
import pyspark.sql.types as T         #Define os tipos nativos do PySpark
import pyspark.sql.functions as F     #Importa as funções nativas do Spark para manipulação dos dados
from pyspark.sql.window import Window #Importa a função utilizada para criação de janelas

# Lendo dados importados para o nosso sistema de arquivos

In [0]:
# Por enquanto não vamos entrar em detalhes sobre o que esses dados significam
df = table("orders")

display(df)

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 53cdb2fc8bc7dce0b6741e2150273451 b0830fb4747a6c6d20dea0b8c802d7ef delivered 2018-07-24 20:41:37 2018-07-26 03:24:27 2018-07-26 14:31:00 2018-08-07 15:27:45 2018-08-13 00:00:00 47770eb9100c2d0c44946d9cf07ec65d 41ce2a54c0b03bf3443c3d931a367089 delivered 2018-08-08 08:38:49 2018-08-08 08:55:23 2018-08-08 13:50:00 2018-08-17 18:06:29 2018-09-04 00:00:00 949d5b44dbf5de918fe9c16f97b45f8a f88197465ea7920adcdbec7375364d82 delivered 2017-11-18 19:28:06 2017-11-18 19:45:59 2017-11-22 13:39:59 2017-12-02 00:28:42 2017-12-15 00:00:00 ad21c59c0840e6cb83a9ceb5573f8159 8ab97904e6daea8866dbdbc4fb7aad2c delivered 2018-02-13 21:18:39 2018-02-13 22:20:29 2018-02-14 19:46:34 2018-02-16 18:17:02 2018-02-26 00:00:00 a4591c265e18cb1dcee52889e2d8acc3 503740e9ca751ccdda7ba28e9ab8f608 delivered 2017-07-09 21:57:05 2017-07-09 22:10:13 2017-07-11 14:58:04 2017-07-26 10:57:55 2017-08-01 00:00:00 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 6514b8ad8028c9f2cc2374ded245783f 9bdf08b4b3b52b5526ff42d37d47f222 delivered 2017-05-16 13:10:30 2017-05-16 13:22:11 2017-05-22 10:07:46 2017-05-26 12:55:51 2017-06-07 00:00:00 76c6e866289321a7c93b82b54852dc33 f54a9f0e6b351c431402b8461ea51999 delivered 2017-01-23 18:29:09 2017-01-25 02:50:47 2017-01-26 14:16:31 2017-02-02 14:08:10 2017-03-06 00:00:00 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 e6ce16cb79ec1d90b1da9085a6118aeb 494dded5b201313c64ed7f100595b95c delivered 2017-05-16 19:41:10 2017-05-16 19:50:18 2017-05-18 11:40:40 2017-05-29 11:18:31 2017-06-07 00:00:00 34513ce0c4fab462a55830c0989c7edb 7711cf624183d843aafe81855097bc37 delivered 2017-07-13 19:58:11 2017-07-13 20:10:08 2017-07-14 18:43:29 2017-07-19 14:04:48 2017-08-08 00:00:00 82566a660a982b15fb86e904c8d32918 d3e3b74c766bc6214e0c830b17ee2341 delivered 2018-06-07 10:06:19 2018-06-09 03:13:12 2018-06-11 13:29:00 2018-06-19 12:05:52 2018-07-18 00:00:00 5ff96c15d0b717ac6ad1f3d77225a350 19402a48fe860416adf93348aba37740 delivered 2018-07-25 17:44:10 2018-07-25 17:55:14 2018-07-26 13:16:00 2018-07-30 15:52:25 2018-08-08 00:00:00 432aaf21d85167c2c86ec9448c4e42cc 3df704f53d3f1d4818840b34ec672a9f delivered 2018-03-01 14:14:28 2018-03-01 15:10:47 2018-03-02 21:09:20 2018-03-12 23:36:26 2018-03-21 00:00:00 dcb36b511fcac050b97cd5c05de84dc3 3b6828a50ffe546942b7a473d70ac0fc delivered 2018-06-07 19:03:12 2018-06-12 23:31:02 2018-06-11 14:54:00 2018-06-21 15:34:32 2018-07-04 00:00:00 403b97836b0c04a622354cf531062e5f 738b086814c6fcc74b8cc583f8516ee3 delivered 2018-01-02 19:00:43 2018-01-02 19:09:04 2018-01-03 18:19:09 2018-01-20 01:38:59 2018-02-06 00:00:00 116f0b09343b49556bbad5f35bee0cdf 3187789bec990987628d7a9beb4dd6ac delivered 2017-12-26 23:41:31 2017-12-26 23:50:22 2017-12-28 18:33:05 2018-01-08 22:36:36 2018-01-29 00:00:00 85ce859fd6dc634de8d2f1e290444043 059f7fc5719c7da6cbafe370971a8d70 delivered 2017-11-21 00:03:41 2017-11-21 00:14:22 2017-11-23 21:32:26 2017-11-27 18:28:00 2017-12-11 00:00:00 83018ec114eee8641c97e08f7b4e926f 7f8c8b9c2ae27bf3300f670c3d478be8 delivered 2017-10-26 15:54:26 2017-10-26 16:08:14 2017-10-26 21:46:53 2017-11-08 22:22:00 2017-11-23 00:00:00 203096f03d82e0dffbc41ebc2e2bcfb7 d2b091571da224a1b36412c18bc3bbfe delivered 2017-09-18 14:31:30 2017-09-19 04:04:09 2017-10-06 17:50:03 2017-10-09 22:23:46 2017-09-28 00:00:00 f848643eec1d69395095eb3840d2051e 4fa1cd166fa598be6de80fa84eaade43 delivered 2018-03-15 08:52:40 2018-03-15 09:09:31 2018-03-15 19:52:48 2018-03-19 18:08:32 2018-03-29 00

Como podemos verificar, o *Databricks* traz dois comandos muitos úteis para leitura e apresentação dos dados:
  
  
 - **table**: esse comando lê um arquivo gravado no sistema de arquivos do nosso *cluster*;
 - **display**: esse comando apresenta os dados de uma forma estilizada.

# Verificando o esquema (tipo de dados em cada uma das colunas)

In [0]:
df.printSchema()

root
 |-- order_id: string (nullable = true)
 |-- customer_id: string (nullable = true)
 |-- order_status: string (nullable = true)
 |-- order_purchase_timestamp: string (nullable = true)
 |-- order_approved_at: string (nullable = true)
 |-- order_delivered_carrier_date: string (nullable = true)
 |-- order_delivered_customer_date: string (nullable = true)
 |-- order_estimated_delivery_date: string (nullable = true)



# Descrição básica do conjunto de dados

In [0]:
display(df.describe())

summary order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date count 99441 99441 99441 99441 99281 97658 96476 99441 mean null null null null null null null null stddev null null null null null null null null min 00010242fe8c5a6d1ba2dd792cb16214 00012a2ce6f8dcda20d059ce98491703 approved 2016-09-04 21:15:19 2016-09-15 12:16:38 2016-10-08 10:34:01 2016-10-11 13:46:32 2016-09-30 00:00:00 max fffe41c64501cc87c801fd61db3f6244 ffffe8b65bbe3087b653a978c870db99 unavailable 2018-10-17 17:30:18 2018-09-03 17:40:06 2018-09-11 19:48:28 2018-10-17 13:22:46 2018-11-12 00:00:00

In [0]:
n_rows = df.count()

print(f"Number of rows in this dataframe: {n_rows}.")

Number of rows in this dataframe: 99441.


# Selecionando colunas

In [0]:
df.select("order_id", "customer_id")

Out[6]: DataFrame[order_id: string, customer_id: string]

### UÉ!? Cada a tabela?

Aqui entramos em um ponto interessante sobre o *Spark*: Ele é **lazy evaluation**, isso significa que ele só apresentará os resultados caso mandemos explicitamente, por meio de uma ação (que avisa ao *Spark* para realizar a computação e devolver os resultados ao *driver*).

Além de ações o Spark também tem transformações (que nunca geram uma saída, somente criam um novo conjunto de dados).

#### Para executar uma transformação propriamente dita, precisamos de uma ação.

Isso se deve porque o *Spark*, internamente, gera um *DAG* (grafo acíclico direcionado), com todas as transformações que realizarmos no nosso conjunto de dados. Isso serve para possibilitar que o mecanismo de otimizção de *queries* opere, definindo o plano de execução físico mais apropriado para nossa *query* de acordo com os passo que definimos.

##### Alguns exemplos de ações:

- count;
- show.


##### Alguns exemplos de transformações:

- select;
- filter;
- groupby.

In [0]:
# Display chama internamente uma ação show, por isso vemos o resultado da nossa transformação select
display(df.select("order_id", "customer_id"))

order_id customer_id e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d 53cdb2fc8bc7dce0b6741e2150273451 b0830fb4747a6c6d20dea0b8c802d7ef 47770eb9100c2d0c44946d9cf07ec65d 41ce2a54c0b03bf3443c3d931a367089 949d5b44dbf5de918fe9c16f97b45f8a f88197465ea7920adcdbec7375364d82 ad21c59c0840e6cb83a9ceb5573f8159 8ab97904e6daea8866dbdbc4fb7aad2c a4591c265e18cb1dcee52889e2d8acc3 503740e9ca751ccdda7ba28e9ab8f608 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a 6514b8ad8028c9f2cc2374ded245783f 9bdf08b4b3b52b5526ff42d37d47f222 76c6e866289321a7c93b82b54852dc33 f54a9f0e6b351c431402b8461ea51999 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d e6ce16cb79ec1d90b1da9085a6118aeb 494dded5b201313c64ed7f100595b95c 34513ce0c4fab462a55830c0989c7edb 7711cf624183d843aafe81855097bc37 82566a660a982b15fb86e904c8d32918 d3e3b74c766bc6214e0c830b17ee2341 5ff96c15d0b717ac6ad1f3d77225a350 19402a48fe860416adf93348aba37740 432aaf21d85167c2c86ec9448c4e42cc 3df704f53d3f1d4818840b34ec672a9f dcb36b511fcac050b97cd5c05de84dc3 3b6828a50ffe546942b7a473d70ac0fc 403b97836b0c04a622354cf531062e5f 738b086814c6fcc74b8cc583f8516ee3 116f0b09343b49556bbad5f35bee0cdf 3187789bec990987628d7a9beb4dd6ac 85ce859fd6dc634de8d2f1e290444043 059f7fc5719c7da6cbafe370971a8d70 83018ec114eee8641c97e08f7b4e926f 7f8c8b9c2ae27bf3300f670c3d478be8 203096f03d82e0dffbc41ebc2e2bcfb7 d2b091571da224a1b36412c18bc3bbfe f848643eec1d69395095eb3840d2051e 4fa1cd166fa598be6de80fa84eaade43 2807d0e504d6d4894d41672727bc139f 72ae281627a6102d9b3718528b420f8a 95266dbfb7e20354baba07964dac78d5 a166da34890074091a942054b36e4265 f3e7c359154d965827355f39d6b1fdac 62b423aab58096ca514ba6aa06be2f98 fbf9ac61453ac646ce8ad9783d7d0af6 3a874b4d4c4b6543206ff5d89287f0c3 acce194856392f074dbf9dada14d8d82 7e20bf5ca92da68200643bda76c504c6 dd78f560c270f1909639c11b925620ea 8b212b9525f9e74e85e37ed6df37693e 91b2a010e1e45e6ba3d133fa997597be cce89a605105b148387c52e286ac8335 ecab90c9933c58908d3d6add7c6f5ae3 761df82feda9778854c6dafdaeb567e4 f70a0aff17df5a6cdd9a7196128bd354 456dc10730fbdba34615447ea195d643 1790eea0b567cf50911c057cf20f90f9 52142aa69d8d0e1247ab0cada0f76023 989225ba6d0ebd5873335f7e01de2ae7 816f8653d5361cbf94e58c33f2502a5c d887b52c6516beb39e8cd44a5f8b60f7 d9ef95f98d8da3b492bb8c0447910498 b276e4f8c0fb86bd82fce576f21713e0 cf8ffeddf027932e51e4eae73b384059 8563039e855156e48fccee4d611a3196 5f16605299d698660e0606f7eae2d2f9 60550084e6b4c0cb89a87df1f3e5ebd9 f5458ddc3545711efa883dd7ae7c4497 5acce57f8d9dfd55fa48e212a641a69d 295ae9b35379e077273387ff64354b6f 434d158e96bdd6972ad6e6d73ddcfd22 2a1dfb647f32f4390e7b857c67458536 7206b86ea789983f7a273ea7fa0bc2a8 3391c4bc11a817e7973e498b0b023158 1e7aff52cdbb2451ace09d0f848c3699 ddaff536587109b89777e0353215e150 6ea2f835b4556291ffdc53fa0b3b95e8 c7340080e394356141681bd4c9b8fe31 948097deef559c742e7ce321e5e58919 8644be24d48806bc3a88fd59fb47ceb1 d22e9fa5731b9e30e8b27afcdc2f8563 756fb9391752dad934e0fe3733378e57 ee64d42b8cf066f35eac1cf57de1aa85 caded193e8e47b8362864762a83db3c5 6ebaec694d7025e2ad4a05dba887c032 4f28355e5c17a4a42d3ce2439a1d4501 d17dc4a904426827ca80f2ccb3a6be56 569cf68214806a39acc0f39344aea67f 25f4376934e13d3508486352e11a5db0 12fd2740039676063a874b9567dfa651 5820a1100976432c7968a52da59e9364 2b56e94c2f66f2d97cfa63356f69cee8 2ce1ad82022c1ba30c2079502ac725aa 7f2178c5d771e17f507d3c1637339298 138849fd84dff2fb4ca70a0a34c4aa1c 9b18f3fc296990b97854e351334a32f6 47aa4816b27ba60ec948cd019cc1afc1 148348ff65384b4249b762579532e248 9faeb9b2746b9d7526aef5acb08e2aa0 79183cd650e2bb0d475b0067d45946ac 641fb0752bf5b5940c376b3a8bb9dc52 f5afca14dfa9dc64251cf2b45c54c363 e425680f760cbc130be3e53a9773c584 f178c1827f67a8467b0385b7378d951a 40c5e18f7d112b59b3e5113a59a905b3 67407057a7d5ee17d1cd09523f484d13 734e7d1bbaeb2ff82521ca0fe6fb6f79 2932d241d1f31e6df6c701d52370ae02 66e4624ae69e7dc89bd50222b59f581f 684fa6da5134b9e4dab731e00011712d a685d016c8a26f71a0bb67821070e398 911e4c37f5cafe1604fe6767034bf1ae 2edfd6d1f0b4cd0db4bf37b1b224d855 241e78de29b3090cfa1b5d73a8130c72 68873cf91053cd11e6b

Podemos ver que o método *.select* é utilizado para realizar a seleção de colunas no conjunto de dados. Outra coisa que podemos notar é a proximidade entre a sintaxe do *PySpark* e a sintaxe do *SQL*.

In [0]:
#Também podemos utilizar funções dentro do nosso método .select além de darmos um alias para o resultado
display(df.select(F.countDistinct(F.col("order_status")).alias("count_distinct_order_status")))

count_distinct_order_status 8

# Filtrando colunas

In [0]:
display(df.filter(F.col("order_status") == "invoiced"))

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 0760a852e4e9d89eb77bf631eaaf1c84 d2a79636084590b7465af8ab374a8cf5 invoiced 2018-08-03 17:44:42 2018-08-07 06:15:14 null null 2018-08-21 00:00:00 38b7efdf33dd5561f4f5d4f6e07b0414 021e84751ba0ead75b6d314a6ead88d9 invoiced 2017-08-01 18:17:41 2017-08-01 18:32:30 null null 2017-08-28 00:00:00 51b0dccc8596ce37a930dff2d63a10a2 31bf1057b00f14804278590bbac18b1b invoiced 2017-05-05 22:34:48 2017-05-05 22:45:12 null null 2017-06-06 00:00:00 5504eaa5a86eb25fa666cf2e6b96c701 a30be38e1ed0ffb39b318bf1d15e98d9 invoiced 2017-11-29 08:33:06 2017-11-29 08:56:23 null null 2017-12-20 00:00:00 c3a6dc9afef5794ea4a867b5a18e0ad1 0c305f688ce08dc9402a2164fd6f29d6 invoiced 2017-11-25 14:10:20 2017-11-25 17:32:57 null null 2017-12-19 00:00:00 566c5bff1142c9d6003a83fd2e8ad1e5 892022d497c9598ce4a313f64ceaa87e invoiced 2017-11-23 18:03:23 2017-11-23 18:25:18 null null 2017-12-18 00:00:00 b4c9f083bce61caf47fb38f9ba058bce 6ce60503e530d8a67926e9b8e3fdb635 invoiced 2017-08-05 16:00:56 2017-08-05 16:15:16 null null 2017-08-30 00:00:00 f029d5966aa03c87e17e2482f86202b1 ece9fb6661a1dc0cd93f5f8c9cf13b83 invoiced 2017-10-23 21:44:36 2017-10-23 21:56:09 null null 2017-11-14 00:00:00 6a828279d73f18174dd3b9c653d5213d c994647aae9a45b8ae6eb75b77354ed3 invoiced 2017-06-25 17:54:26 2017-06-25 18:05:22 null null 2017-07-14 00:00:00 be33d865802b05e364fc5f46166e5acf 1a002323bd40f93378ee1824e2343798 invoiced 2018-04-03 13:55:48 2018-04-04 03:29:18 null null 2018-04-27 00:00:00 e9376d90b28f9cdea83d4d850e4bb1a7 faafae37ddb3e4af81c10a397bcca35f invoiced 2017-09-01 15:02:24 2017-09-01 15:15:30 null null 2017-09-15 00:00:00 853eb57e7109781f60bfaec58c70c258 fac697cc750bbd1acf6dc02ccfd6adb7 invoiced 2017-04-23 13:25:43 2017-04-23 13:35:18 null null 2017-05-26 00:00:00 ac61010b8d348d62726ebfe687b026f6 c84b87889fc766cdf27534805e07f502 invoiced 2017-05-26 15:26:26 2017-05-26 15:42:26 null null 2017-06-19 00:00:00 360787554f41824600bdcba9687cd4f0 c1474a24d28e0702ff76d03b5fd3bbe6 invoiced 2018-03-23 19:39:46 2018-03-23 19:50:29 null null 2018-04-16 00:00:00 81b6015857004cedcfbc04ae95d7bfe5 e48db55564959abae4213119668090b8 invoiced 2018-03-10 09:52:29 2018-03-10 10:27:59 null null 2018-03-28 00:00:00 315f7759c3f6557f50e47798ccd673a3 54e217beb4b07ffdebc14c428e3f240d invoiced 2018-01-13 15:18:00 2018-01-15 10:11:08 null null 2018-02-08 00:00:00 1e0f40bbfe787796d0c56e3795dc94d8 df1e522fe10d104e337d07d3ba3ff108 invoiced 2018-08-06 20:17:25 2018-08-06 20:30:10 null null 2018-08-09 00:00:00 0b43acd81f6d3f30136133517a13b72f dee7ac1315330a02d049ad3b108c7ad4 invoiced 2017-12-03 17:15:08 2017-12-03 17:34:28 null null 2017-12-27 00:00:00 2e90d155b85776a842b3b1c59aa4b340 dc0f64fb88e567f9d8ff195dcc36f332 invoiced 2017-05-06 19:09:33 2017-05-06 19:22:04 null null 2017-06-09 00:00:00 0d0665d64b4dd1dae2ed97fa92509144 831f66f86273e58c41a61f27987bbc13 invoiced 2018-04-24 09:19:11 2018-04-24 17:53:10 null null 2018-05-16 00:00:00 2d372207e6e6c38c19f44bf5a7e07e66 dd4f9db38b8a3f03ff4dd5f159dfe50a invoiced 2018-03-15 16:34:31 2018-03-15 17:10:11 null null 2018-04-06 00:00:00 e6d7920ba4f7a2673a980bd60d46cb53 b7bec5d1581b731f6404c0cb57a70631 invoiced 2018-07-31 14:15:30 2018-08-02 05:05:13 null null 2018-08-17 00:00:00 90861ef1f4e7a006095e1d5dd38f2195 49a5cb9469b39dffb92314ebff1efd28 invoiced 2017-04-25 20:38:07 2017-04-25 20:50:20 null null 2017-05-12 00:00:00 81ad0542f902d06936247fe96fb102f8 7da197a421555f9d5858c2a35ec19f2f invoiced 2017-11-08 10:52:52 2017-11-08 11:06:41 null null 2017-12-01 00:00:00 e63f16fab229756ce58f86d40747944e 0c8fca0ebf003ce1352d04675da28d70 invoiced 2017-12-11 12:22:24 2017-12-11 12:31:01 null null 2018-01-12 00:00:00 f351ab7501d0f1d1874843df793c2fa6 39ca314818a8fcf7275bdd62444be65

Algumas pessoas utilizam o método *.where* em vez do método *.filter*. Ambos fazem a mesma coisa, sendo o *.where* definido como um *alias* para o método *.filter*.

##### Agora que passamos por alguns comandos, vamos ver algumas variações que a sintaxe permite:

In [0]:
#Algumas pessoas utilizam a seguinte sintaxe:
display(df.filter('order_status == "invoiced"'))

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 0760a852e4e9d89eb77bf631eaaf1c84 d2a79636084590b7465af8ab374a8cf5 invoiced 2018-08-03 17:44:42 2018-08-07 06:15:14 null null 2018-08-21 00:00:00 38b7efdf33dd5561f4f5d4f6e07b0414 021e84751ba0ead75b6d314a6ead88d9 invoiced 2017-08-01 18:17:41 2017-08-01 18:32:30 null null 2017-08-28 00:00:00 51b0dccc8596ce37a930dff2d63a10a2 31bf1057b00f14804278590bbac18b1b invoiced 2017-05-05 22:34:48 2017-05-05 22:45:12 null null 2017-06-06 00:00:00 5504eaa5a86eb25fa666cf2e6b96c701 a30be38e1ed0ffb39b318bf1d15e98d9 invoiced 2017-11-29 08:33:06 2017-11-29 08:56:23 null null 2017-12-20 00:00:00 c3a6dc9afef5794ea4a867b5a18e0ad1 0c305f688ce08dc9402a2164fd6f29d6 invoiced 2017-11-25 14:10:20 2017-11-25 17:32:57 null null 2017-12-19 00:00:00 566c5bff1142c9d6003a83fd2e8ad1e5 892022d497c9598ce4a313f64ceaa87e invoiced 2017-11-23 18:03:23 2017-11-23 18:25:18 null null 2017-12-18 00:00:00 b4c9f083bce61caf47fb38f9ba058bce 6ce60503e530d8a67926e9b8e3fdb635 invoiced 2017-08-05 16:00:56 2017-08-05 16:15:16 null null 2017-08-30 00:00:00 f029d5966aa03c87e17e2482f86202b1 ece9fb6661a1dc0cd93f5f8c9cf13b83 invoiced 2017-10-23 21:44:36 2017-10-23 21:56:09 null null 2017-11-14 00:00:00 6a828279d73f18174dd3b9c653d5213d c994647aae9a45b8ae6eb75b77354ed3 invoiced 2017-06-25 17:54:26 2017-06-25 18:05:22 null null 2017-07-14 00:00:00 be33d865802b05e364fc5f46166e5acf 1a002323bd40f93378ee1824e2343798 invoiced 2018-04-03 13:55:48 2018-04-04 03:29:18 null null 2018-04-27 00:00:00 e9376d90b28f9cdea83d4d850e4bb1a7 faafae37ddb3e4af81c10a397bcca35f invoiced 2017-09-01 15:02:24 2017-09-01 15:15:30 null null 2017-09-15 00:00:00 853eb57e7109781f60bfaec58c70c258 fac697cc750bbd1acf6dc02ccfd6adb7 invoiced 2017-04-23 13:25:43 2017-04-23 13:35:18 null null 2017-05-26 00:00:00 ac61010b8d348d62726ebfe687b026f6 c84b87889fc766cdf27534805e07f502 invoiced 2017-05-26 15:26:26 2017-05-26 15:42:26 null null 2017-06-19 00:00:00 360787554f41824600bdcba9687cd4f0 c1474a24d28e0702ff76d03b5fd3bbe6 invoiced 2018-03-23 19:39:46 2018-03-23 19:50:29 null null 2018-04-16 00:00:00 81b6015857004cedcfbc04ae95d7bfe5 e48db55564959abae4213119668090b8 invoiced 2018-03-10 09:52:29 2018-03-10 10:27:59 null null 2018-03-28 00:00:00 315f7759c3f6557f50e47798ccd673a3 54e217beb4b07ffdebc14c428e3f240d invoiced 2018-01-13 15:18:00 2018-01-15 10:11:08 null null 2018-02-08 00:00:00 1e0f40bbfe787796d0c56e3795dc94d8 df1e522fe10d104e337d07d3ba3ff108 invoiced 2018-08-06 20:17:25 2018-08-06 20:30:10 null null 2018-08-09 00:00:00 0b43acd81f6d3f30136133517a13b72f dee7ac1315330a02d049ad3b108c7ad4 invoiced 2017-12-03 17:15:08 2017-12-03 17:34:28 null null 2017-12-27 00:00:00 2e90d155b85776a842b3b1c59aa4b340 dc0f64fb88e567f9d8ff195dcc36f332 invoiced 2017-05-06 19:09:33 2017-05-06 19:22:04 null null 2017-06-09 00:00:00 0d0665d64b4dd1dae2ed97fa92509144 831f66f86273e58c41a61f27987bbc13 invoiced 2018-04-24 09:19:11 2018-04-24 17:53:10 null null 2018-05-16 00:00:00 2d372207e6e6c38c19f44bf5a7e07e66 dd4f9db38b8a3f03ff4dd5f159dfe50a invoiced 2018-03-15 16:34:31 2018-03-15 17:10:11 null null 2018-04-06 00:00:00 e6d7920ba4f7a2673a980bd60d46cb53 b7bec5d1581b731f6404c0cb57a70631 invoiced 2018-07-31 14:15:30 2018-08-02 05:05:13 null null 2018-08-17 00:00:00 90861ef1f4e7a006095e1d5dd38f2195 49a5cb9469b39dffb92314ebff1efd28 invoiced 2017-04-25 20:38:07 2017-04-25 20:50:20 null null 2017-05-12 00:00:00 81ad0542f902d06936247fe96fb102f8 7da197a421555f9d5858c2a35ec19f2f invoiced 2017-11-08 10:52:52 2017-11-08 11:06:41 null null 2017-12-01 00:00:00 e63f16fab229756ce58f86d40747944e 0c8fca0ebf003ce1352d04675da28d70 invoiced 2017-12-11 12:22:24 2017-12-11 12:31:01 null null 2018-01-12 00:00:00 f351ab7501d0f1d1874843df793c2fa6 39ca314818a8fcf7275bdd62444be65

### Também podemos utilizar código SQL, de duas formas:

In [0]:
%sql

SELECT * FROM orders

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 53cdb2fc8bc7dce0b6741e2150273451 b0830fb4747a6c6d20dea0b8c802d7ef delivered 2018-07-24 20:41:37 2018-07-26 03:24:27 2018-07-26 14:31:00 2018-08-07 15:27:45 2018-08-13 00:00:00 47770eb9100c2d0c44946d9cf07ec65d 41ce2a54c0b03bf3443c3d931a367089 delivered 2018-08-08 08:38:49 2018-08-08 08:55:23 2018-08-08 13:50:00 2018-08-17 18:06:29 2018-09-04 00:00:00 949d5b44dbf5de918fe9c16f97b45f8a f88197465ea7920adcdbec7375364d82 delivered 2017-11-18 19:28:06 2017-11-18 19:45:59 2017-11-22 13:39:59 2017-12-02 00:28:42 2017-12-15 00:00:00 ad21c59c0840e6cb83a9ceb5573f8159 8ab97904e6daea8866dbdbc4fb7aad2c delivered 2018-02-13 21:18:39 2018-02-13 22:20:29 2018-02-14 19:46:34 2018-02-16 18:17:02 2018-02-26 00:00:00 a4591c265e18cb1dcee52889e2d8acc3 503740e9ca751ccdda7ba28e9ab8f608 delivered 2017-07-09 21:57:05 2017-07-09 22:10:13 2017-07-11 14:58:04 2017-07-26 10:57:55 2017-08-01 00:00:00 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 6514b8ad8028c9f2cc2374ded245783f 9bdf08b4b3b52b5526ff42d37d47f222 delivered 2017-05-16 13:10:30 2017-05-16 13:22:11 2017-05-22 10:07:46 2017-05-26 12:55:51 2017-06-07 00:00:00 76c6e866289321a7c93b82b54852dc33 f54a9f0e6b351c431402b8461ea51999 delivered 2017-01-23 18:29:09 2017-01-25 02:50:47 2017-01-26 14:16:31 2017-02-02 14:08:10 2017-03-06 00:00:00 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 e6ce16cb79ec1d90b1da9085a6118aeb 494dded5b201313c64ed7f100595b95c delivered 2017-05-16 19:41:10 2017-05-16 19:50:18 2017-05-18 11:40:40 2017-05-29 11:18:31 2017-06-07 00:00:00 34513ce0c4fab462a55830c0989c7edb 7711cf624183d843aafe81855097bc37 delivered 2017-07-13 19:58:11 2017-07-13 20:10:08 2017-07-14 18:43:29 2017-07-19 14:04:48 2017-08-08 00:00:00 82566a660a982b15fb86e904c8d32918 d3e3b74c766bc6214e0c830b17ee2341 delivered 2018-06-07 10:06:19 2018-06-09 03:13:12 2018-06-11 13:29:00 2018-06-19 12:05:52 2018-07-18 00:00:00 5ff96c15d0b717ac6ad1f3d77225a350 19402a48fe860416adf93348aba37740 delivered 2018-07-25 17:44:10 2018-07-25 17:55:14 2018-07-26 13:16:00 2018-07-30 15:52:25 2018-08-08 00:00:00 432aaf21d85167c2c86ec9448c4e42cc 3df704f53d3f1d4818840b34ec672a9f delivered 2018-03-01 14:14:28 2018-03-01 15:10:47 2018-03-02 21:09:20 2018-03-12 23:36:26 2018-03-21 00:00:00 dcb36b511fcac050b97cd5c05de84dc3 3b6828a50ffe546942b7a473d70ac0fc delivered 2018-06-07 19:03:12 2018-06-12 23:31:02 2018-06-11 14:54:00 2018-06-21 15:34:32 2018-07-04 00:00:00 403b97836b0c04a622354cf531062e5f 738b086814c6fcc74b8cc583f8516ee3 delivered 2018-01-02 19:00:43 2018-01-02 19:09:04 2018-01-03 18:19:09 2018-01-20 01:38:59 2018-02-06 00:00:00 116f0b09343b49556bbad5f35bee0cdf 3187789bec990987628d7a9beb4dd6ac delivered 2017-12-26 23:41:31 2017-12-26 23:50:22 2017-12-28 18:33:05 2018-01-08 22:36:36 2018-01-29 00:00:00 85ce859fd6dc634de8d2f1e290444043 059f7fc5719c7da6cbafe370971a8d70 delivered 2017-11-21 00:03:41 2017-11-21 00:14:22 2017-11-23 21:32:26 2017-11-27 18:28:00 2017-12-11 00:00:00 83018ec114eee8641c97e08f7b4e926f 7f8c8b9c2ae27bf3300f670c3d478be8 delivered 2017-10-26 15:54:26 2017-10-26 16:08:14 2017-10-26 21:46:53 2017-11-08 22:22:00 2017-11-23 00:00:00 203096f03d82e0dffbc41ebc2e2bcfb7 d2b091571da224a1b36412c18bc3bbfe delivered 2017-09-18 14:31:30 2017-09-19 04:04:09 2017-10-06 17:50:03 2017-10-09 22:23:46 2017-09-28 00:00:00 f848643eec1d69395095eb3840d2051e 4fa1cd166fa598be6de80fa84eaade43 delivered 2018-03-15 08:52:40 2018-03-15 09:09:31 2018-03-15 19:52:48 2018-03-19 18:08:32 2018-03-29 00

In [0]:
#Também podemos executar código SQL dessa forma
spark.sql("SELECT * FROM orders")

Out[6]: DataFrame[order_id: string, customer_id: string, order_status: string, order_purchase_timestamp: string, order_approved_at: string, order_delivered_carrier_date: string, order_delivered_customer_date: string, order_estimated_delivery_date: string]

Dependendo de como você carregar os seus dados, as tabelas precisarão ser registradas como uma *view*:

```
df.createOrReplaceTempView("test")
```

E após isso suas *queries* podem ser executadas normalmente.

**OBS.:** Essa *view* tem duração atrelada a sua *SparkSession* (que não entraremos em detalhes nesse tutorial).

# Criando colunas

Para criamos colunas vamos utilizar o método *.withColumn*. Esse método necessita de dois parâmetros, o nome da nova coluna e o conteúdo da mesma.

In [0]:
#Criando uma coluna test e preenchedo ela com o LITERAL 1 (importante notar isso)
display(df.withColumn("test", F.lit(1)))

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date test e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 1 53cdb2fc8bc7dce0b6741e2150273451 b0830fb4747a6c6d20dea0b8c802d7ef delivered 2018-07-24 20:41:37 2018-07-26 03:24:27 2018-07-26 14:31:00 2018-08-07 15:27:45 2018-08-13 00:00:00 1 47770eb9100c2d0c44946d9cf07ec65d 41ce2a54c0b03bf3443c3d931a367089 delivered 2018-08-08 08:38:49 2018-08-08 08:55:23 2018-08-08 13:50:00 2018-08-17 18:06:29 2018-09-04 00:00:00 1 949d5b44dbf5de918fe9c16f97b45f8a f88197465ea7920adcdbec7375364d82 delivered 2017-11-18 19:28:06 2017-11-18 19:45:59 2017-11-22 13:39:59 2017-12-02 00:28:42 2017-12-15 00:00:00 1 ad21c59c0840e6cb83a9ceb5573f8159 8ab97904e6daea8866dbdbc4fb7aad2c delivered 2018-02-13 21:18:39 2018-02-13 22:20:29 2018-02-14 19:46:34 2018-02-16 18:17:02 2018-02-26 00:00:00 1 a4591c265e18cb1dcee52889e2d8acc3 503740e9ca751ccdda7ba28e9ab8f608 delivered 2017-07-09 21:57:05 2017-07-09 22:10:13 2017-07-11 14:58:04 2017-07-26 10:57:55 2017-08-01 00:00:00 1 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 1 6514b8ad8028c9f2cc2374ded245783f 9bdf08b4b3b52b5526ff42d37d47f222 delivered 2017-05-16 13:10:30 2017-05-16 13:22:11 2017-05-22 10:07:46 2017-05-26 12:55:51 2017-06-07 00:00:00 1 76c6e866289321a7c93b82b54852dc33 f54a9f0e6b351c431402b8461ea51999 delivered 2017-01-23 18:29:09 2017-01-25 02:50:47 2017-01-26 14:16:31 2017-02-02 14:08:10 2017-03-06 00:00:00 1 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 1 e6ce16cb79ec1d90b1da9085a6118aeb 494dded5b201313c64ed7f100595b95c delivered 2017-05-16 19:41:10 2017-05-16 19:50:18 2017-05-18 11:40:40 2017-05-29 11:18:31 2017-06-07 00:00:00 1 34513ce0c4fab462a55830c0989c7edb 7711cf624183d843aafe81855097bc37 delivered 2017-07-13 19:58:11 2017-07-13 20:10:08 2017-07-14 18:43:29 2017-07-19 14:04:48 2017-08-08 00:00:00 1 82566a660a982b15fb86e904c8d32918 d3e3b74c766bc6214e0c830b17ee2341 delivered 2018-06-07 10:06:19 2018-06-09 03:13:12 2018-06-11 13:29:00 2018-06-19 12:05:52 2018-07-18 00:00:00 1 5ff96c15d0b717ac6ad1f3d77225a350 19402a48fe860416adf93348aba37740 delivered 2018-07-25 17:44:10 2018-07-25 17:55:14 2018-07-26 13:16:00 2018-07-30 15:52:25 2018-08-08 00:00:00 1 432aaf21d85167c2c86ec9448c4e42cc 3df704f53d3f1d4818840b34ec672a9f delivered 2018-03-01 14:14:28 2018-03-01 15:10:47 2018-03-02 21:09:20 2018-03-12 23:36:26 2018-03-21 00:00:00 1 dcb36b511fcac050b97cd5c05de84dc3 3b6828a50ffe546942b7a473d70ac0fc delivered 2018-06-07 19:03:12 2018-06-12 23:31:02 2018-06-11 14:54:00 2018-06-21 15:34:32 2018-07-04 00:00:00 1 403b97836b0c04a622354cf531062e5f 738b086814c6fcc74b8cc583f8516ee3 delivered 2018-01-02 19:00:43 2018-01-02 19:09:04 2018-01-03 18:19:09 2018-01-20 01:38:59 2018-02-06 00:00:00 1 116f0b09343b49556bbad5f35bee0cdf 3187789bec990987628d7a9beb4dd6ac delivered 2017-12-26 23:41:31 2017-12-26 23:50:22 2017-12-28 18:33:05 2018-01-08 22:36:36 2018-01-29 00:00:00 1 85ce859fd6dc634de8d2f1e290444043 059f7fc5719c7da6cbafe370971a8d70 delivered 2017-11-21 00:03:41 2017-11-21 00:14:22 2017-11-23 21:32:26 2017-11-27 18:28:00 2017-12-11 00:00:00 1 83018ec114eee8641c97e08f7b4e926f 7f8c8b9c2ae27bf3300f670c3d478be8 delivered 2017-10-26 15:54:26 2017-10-26 16:08:14 2017-10-26 21:46:53 2017-11-08 22:22:00 2017-11-23 00:00:00 1 203096f03d82e0dffbc41ebc2e2bcfb7 d2b091571da224a1b36412c18bc3bbfe delivered 2017-09-18 14:31:30 2017-09-19 04:04:09 2017-10-06 17:50:03 2017-10-09 22:23:46 2017-09-28 00:00:00 1 f848643eec1d69395095eb3840d2051e 4fa1cd166fa598be6de80fa84eaade43 delivered 2018-03-15 08:52:40 2018-03-15 09:09:31 2018-0

Para utilizarmos as funções nativas do *PySpark* vamos criar uma coluna igual ao ano que a ordem de compra foi criada.

In [0]:
df = df.withColumn("order_purchase_year", F.year(F.col("order_purchase_timestamp")))

display(df)

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date order_purchase_year e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 2017 53cdb2fc8bc7dce0b6741e2150273451 b0830fb4747a6c6d20dea0b8c802d7ef delivered 2018-07-24 20:41:37 2018-07-26 03:24:27 2018-07-26 14:31:00 2018-08-07 15:27:45 2018-08-13 00:00:00 2018 47770eb9100c2d0c44946d9cf07ec65d 41ce2a54c0b03bf3443c3d931a367089 delivered 2018-08-08 08:38:49 2018-08-08 08:55:23 2018-08-08 13:50:00 2018-08-17 18:06:29 2018-09-04 00:00:00 2018 949d5b44dbf5de918fe9c16f97b45f8a f88197465ea7920adcdbec7375364d82 delivered 2017-11-18 19:28:06 2017-11-18 19:45:59 2017-11-22 13:39:59 2017-12-02 00:28:42 2017-12-15 00:00:00 2017 ad21c59c0840e6cb83a9ceb5573f8159 8ab97904e6daea8866dbdbc4fb7aad2c delivered 2018-02-13 21:18:39 2018-02-13 22:20:29 2018-02-14 19:46:34 2018-02-16 18:17:02 2018-02-26 00:00:00 2018 a4591c265e18cb1dcee52889e2d8acc3 503740e9ca751ccdda7ba28e9ab8f608 delivered 2017-07-09 21:57:05 2017-07-09 22:10:13 2017-07-11 14:58:04 2017-07-26 10:57:55 2017-08-01 00:00:00 2017 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 2017 6514b8ad8028c9f2cc2374ded245783f 9bdf08b4b3b52b5526ff42d37d47f222 delivered 2017-05-16 13:10:30 2017-05-16 13:22:11 2017-05-22 10:07:46 2017-05-26 12:55:51 2017-06-07 00:00:00 2017 76c6e866289321a7c93b82b54852dc33 f54a9f0e6b351c431402b8461ea51999 delivered 2017-01-23 18:29:09 2017-01-25 02:50:47 2017-01-26 14:16:31 2017-02-02 14:08:10 2017-03-06 00:00:00 2017 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 2017 e6ce16cb79ec1d90b1da9085a6118aeb 494dded5b201313c64ed7f100595b95c delivered 2017-05-16 19:41:10 2017-05-16 19:50:18 2017-05-18 11:40:40 2017-05-29 11:18:31 2017-06-07 00:00:00 2017 34513ce0c4fab462a55830c0989c7edb 7711cf624183d843aafe81855097bc37 delivered 2017-07-13 19:58:11 2017-07-13 20:10:08 2017-07-14 18:43:29 2017-07-19 14:04:48 2017-08-08 00:00:00 2017 82566a660a982b15fb86e904c8d32918 d3e3b74c766bc6214e0c830b17ee2341 delivered 2018-06-07 10:06:19 2018-06-09 03:13:12 2018-06-11 13:29:00 2018-06-19 12:05:52 2018-07-18 00:00:00 2018 5ff96c15d0b717ac6ad1f3d77225a350 19402a48fe860416adf93348aba37740 delivered 2018-07-25 17:44:10 2018-07-25 17:55:14 2018-07-26 13:16:00 2018-07-30 15:52:25 2018-08-08 00:00:00 2018 432aaf21d85167c2c86ec9448c4e42cc 3df704f53d3f1d4818840b34ec672a9f delivered 2018-03-01 14:14:28 2018-03-01 15:10:47 2018-03-02 21:09:20 2018-03-12 23:36:26 2018-03-21 00:00:00 2018 dcb36b511fcac050b97cd5c05de84dc3 3b6828a50ffe546942b7a473d70ac0fc delivered 2018-06-07 19:03:12 2018-06-12 23:31:02 2018-06-11 14:54:00 2018-06-21 15:34:32 2018-07-04 00:00:00 2018 403b97836b0c04a622354cf531062e5f 738b086814c6fcc74b8cc583f8516ee3 delivered 2018-01-02 19:00:43 2018-01-02 19:09:04 2018-01-03 18:19:09 2018-01-20 01:38:59 2018-02-06 00:00:00 2018 116f0b09343b49556bbad5f35bee0cdf 3187789bec990987628d7a9beb4dd6ac delivered 2017-12-26 23:41:31 2017-12-26 23:50:22 2017-12-28 18:33:05 2018-01-08 22:36:36 2018-01-29 00:00:00 2017 85ce859fd6dc634de8d2f1e290444043 059f7fc5719c7da6cbafe370971a8d70 delivered 2017-11-21 00:03:41 2017-11-21 00:14:22 2017-11-23 21:32:26 2017-11-27 18:28:00 2017-12-11 00:00:00 2017 83018ec114eee8641c97e08f7b4e926f 7f8c8b9c2ae27bf3300f670c3d478be8 delivered 2017-10-26 15:54:26 2017-10-26 16:08:14 2017-10-26 21:46:53 2017-11-08 22:22:00 2017-11-23 00:00:00 2017 203096f03d82e0dffbc41ebc2e2bcfb7 d2b091571da224a1b36412c18bc3bbfe delivered 2017-09-18 14:31:30 2017-09-19 04:04:09 2017-10-06 17:50:03 2017-10-09 22:23:46 2017-09-28 00:00:00 2017 f848643eec1d69395095eb3840d2051e 4fa1cd166fa

In [0]:
# Também podemos realizar outras operações, como a subtração entre duas datas
df = df.withColumn("diff_in_days_between_purchase_and_approved", F.datediff(F.col("order_approved_at"), F.col("order_purchase_timestamp")))

display(df)

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date order_purchase_year diff_in_days_between_purchase_and_approved e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 2017 0 53cdb2fc8bc7dce0b6741e2150273451 b0830fb4747a6c6d20dea0b8c802d7ef delivered 2018-07-24 20:41:37 2018-07-26 03:24:27 2018-07-26 14:31:00 2018-08-07 15:27:45 2018-08-13 00:00:00 2018 2 47770eb9100c2d0c44946d9cf07ec65d 41ce2a54c0b03bf3443c3d931a367089 delivered 2018-08-08 08:38:49 2018-08-08 08:55:23 2018-08-08 13:50:00 2018-08-17 18:06:29 2018-09-04 00:00:00 2018 0 949d5b44dbf5de918fe9c16f97b45f8a f88197465ea7920adcdbec7375364d82 delivered 2017-11-18 19:28:06 2017-11-18 19:45:59 2017-11-22 13:39:59 2017-12-02 00:28:42 2017-12-15 00:00:00 2017 0 ad21c59c0840e6cb83a9ceb5573f8159 8ab97904e6daea8866dbdbc4fb7aad2c delivered 2018-02-13 21:18:39 2018-02-13 22:20:29 2018-02-14 19:46:34 2018-02-16 18:17:02 2018-02-26 00:00:00 2018 0 a4591c265e18cb1dcee52889e2d8acc3 503740e9ca751ccdda7ba28e9ab8f608 delivered 2017-07-09 21:57:05 2017-07-09 22:10:13 2017-07-11 14:58:04 2017-07-26 10:57:55 2017-08-01 00:00:00 2017 0 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 2017 2 6514b8ad8028c9f2cc2374ded245783f 9bdf08b4b3b52b5526ff42d37d47f222 delivered 2017-05-16 13:10:30 2017-05-16 13:22:11 2017-05-22 10:07:46 2017-05-26 12:55:51 2017-06-07 00:00:00 2017 0 76c6e866289321a7c93b82b54852dc33 f54a9f0e6b351c431402b8461ea51999 delivered 2017-01-23 18:29:09 2017-01-25 02:50:47 2017-01-26 14:16:31 2017-02-02 14:08:10 2017-03-06 00:00:00 2017 2 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 2017 0 e6ce16cb79ec1d90b1da9085a6118aeb 494dded5b201313c64ed7f100595b95c delivered 2017-05-16 19:41:10 2017-05-16 19:50:18 2017-05-18 11:40:40 2017-05-29 11:18:31 2017-06-07 00:00:00 2017 0 34513ce0c4fab462a55830c0989c7edb 7711cf624183d843aafe81855097bc37 delivered 2017-07-13 19:58:11 2017-07-13 20:10:08 2017-07-14 18:43:29 2017-07-19 14:04:48 2017-08-08 00:00:00 2017 0 82566a660a982b15fb86e904c8d32918 d3e3b74c766bc6214e0c830b17ee2341 delivered 2018-06-07 10:06:19 2018-06-09 03:13:12 2018-06-11 13:29:00 2018-06-19 12:05:52 2018-07-18 00:00:00 2018 2 5ff96c15d0b717ac6ad1f3d77225a350 19402a48fe860416adf93348aba37740 delivered 2018-07-25 17:44:10 2018-07-25 17:55:14 2018-07-26 13:16:00 2018-07-30 15:52:25 2018-08-08 00:00:00 2018 0 432aaf21d85167c2c86ec9448c4e42cc 3df704f53d3f1d4818840b34ec672a9f delivered 2018-03-01 14:14:28 2018-03-01 15:10:47 2018-03-02 21:09:20 2018-03-12 23:36:26 2018-03-21 00:00:00 2018 0 dcb36b511fcac050b97cd5c05de84dc3 3b6828a50ffe546942b7a473d70ac0fc delivered 2018-06-07 19:03:12 2018-06-12 23:31:02 2018-06-11 14:54:00 2018-06-21 15:34:32 2018-07-04 00:00:00 2018 5 403b97836b0c04a622354cf531062e5f 738b086814c6fcc74b8cc583f8516ee3 delivered 2018-01-02 19:00:43 2018-01-02 19:09:04 2018-01-03 18:19:09 2018-01-20 01:38:59 2018-02-06 00:00:00 2018 0 116f0b09343b49556bbad5f35bee0cdf 3187789bec990987628d7a9beb4dd6ac delivered 2017-12-26 23:41:31 2017-12-26 23:50:22 2017-12-28 18:33:05 2018-01-08 22:36:36 2018-01-29 00:00:00 2017 0 85ce859fd6dc634de8d2f1e290444043 059f7fc5719c7da6cbafe370971a8d70 delivered 2017-11-21 00:03:41 2017-11-21 00:14:22 2017-11-23 21:32:26 2017-11-27 18:28:00 2017-12-11 00:00:00 2017 0 83018ec114eee8641c97e08f7b4e926f 7f8c8b9c2ae27bf3300f670c3d478be8 delivered 2017-10-26 15:54:26 2017-10-26 16:08:14 2017-10-26 21:46:53 2017-11-08 22:22:00 2017-11-23 00:00:00 2017 0 203096f03d82e0dffbc41ebc2e2bcfb7 d2b091571da224a1b36412c18bc3bbfe delivered 2017-09-18 14:31:30 2017-09-19 04:04:09 2017-10-06 17:50:03 2017-1

Todas as função nativas do *PySpark* estão dentro do módulo *functions*, vale a pena explorar.

## Vamos brincar um pouco com a otimização de *queries* do *Spark*?

Para isso vamos simular um conjunto de transformações simples:

- Criamos uma coluna *test* e atribuímos a ela o valor 10;
- Após isso adicionamos 20 ao valor presente na coluna;
- Por fim, adicionamos 30 ao valor presente na coluna.

In [0]:
temp_df = table("orders")

temp_df = temp_df.withColumn("test", F.lit(10))
temp_df = temp_df.withColumn("test", F.col("test") + F.lit(20))
temp_df = temp_df.withColumn("test", F.col("test") + F.lit(30))

temp_df.explain(mode="extended")

== Parsed Logical Plan ==
'Project [order_id#1231, customer_id#1232, order_status#1233, order_purchase_timestamp#1234, order_approved_at#1235, order_delivered_carrier_date#1236, order_delivered_customer_date#1237, order_estimated_delivery_date#1238, ('test + 30) AS test#2368]
+- Project [order_id#1231, customer_id#1232, order_status#1233, order_purchase_timestamp#1234, order_approved_at#1235, order_delivered_carrier_date#1236, order_delivered_customer_date#1237, order_estimated_delivery_date#1238, (test#2348 + 20) AS test#2358]
   +- Project [order_id#1231, customer_id#1232, order_status#1233, order_purchase_timestamp#1234, order_approved_at#1235, order_delivered_carrier_date#1236, order_delivered_customer_date#1237, order_estimated_delivery_date#1238, 10 AS test#2348]
      +- SubqueryAlias spark_catalog.default.orders
         +- Relation[order_id#1231,customer_id#1232,order_status#1233,order_purchase_timestamp#1234,order_approved_at#1235,order_delivered_carrier_date#1236,order_deliv

Nosso plano lógico em detalhes (o plano lógico é a *query* que você escreveu):

**OBS.: Deve ser lido de baixo para cima.**

```
== Analyzed Logical Plan ==
Project [(test#4207 + 30) AS test#4217]
+- Project [(test#4197 + 20) AS test#4207]
   +- Project [ 10 AS test#4197]
```


Nosso plano físico (otimizado):

```
*(1) Project [60 AS test#4217]
```

O otimizador substitui nossas três operações por uma resultante, mais simplificada (que no caso é basicamente atribuir o valor 60 a coluna *test*).

###Trabalhando com GroupBy

In [0]:
#Podemos realizar contagens da quantidade de linhas em cada grupo dessa forma
display(df.groupby("order_status").count())

order_status count shipped 1107 canceled 625 invoiced 314 created 5 delivered 96478 unavailable 609 processing 301 approved 2

In [0]:
# Outra forma de reescrevermos o código acima é:
display(df.groupby("order_status").agg(F.count(F.col("*"))))

order_status count(1) shipped 1107 canceled 625 invoiced 314 created 5 delivered 96478 unavailable 609 processing 301 approved 2

In [0]:
# Renomeando a coluna com a contagem
display(df.groupby("order_status").agg(F.count(F.col("*")).alias("count")))

order_status count shipped 1107 canceled 625 invoiced 314 created 5 delivered 96478 unavailable 609 processing 301 approved 2

*groupby* utilizando o método *.agg* é muito mais geral, podendo ser utilizado em diversas situações. Reparem o uso do método *.alias* para renomear a coluna.

#Joins

*Joins* são extremamente importantes para quem trabalha com bancos de dados. Por sorte, o *PySpark* fornece uma forma concisa e elegante de se trabalhar com esse tipo de operação.

O método que devemos utilizar é o *.join*.

Esse método nos permite definir:

- As colunas que serão utilizadas para o *join* a partir do parâmetro *on* (esse parâmetro também aceita condições lógicas, podendo ser usado para criação de *joins* condicionais);
- O tipo de *join* (*left*, *right* etc).

Para esse exemplo vamos carregar a tabela *customers*.

- Vamos carregar essa tabela da forma clássica (sem o uso da função *table*).

In [0]:
#Repare que passamos a opção "header". Para alterar o separador utilizaríamos a opção "delimiter" e o delimitador necessário (que por padrão é ",")
customers = spark.read.option("header", True).csv("/FileStore/tables/customers_database.csv")

display(customers)

customer_id customer_unique_id customer_zip_code_prefix customer_city customer_state 06b8999e2fba1a1fbc88172c00ba8bc7 861eff4711a542e4b93843c6dd7febb0 14409 franca SP 18955e83d337fd6b2def6b18a428ac77 290c77bc529b7ac935b93aa66c333dc3 09790 sao bernardo do campo SP 4e7b3e00288586ebd08712fdd0374a03 060e732b5b29e8181a18229c7b0b2b5e 01151 sao paulo SP b2b6027bc5c5109e529d4dc6358b12c3 259dac757896d24d7702b9acbbff3f3c 08775 mogi das cruzes SP 4f2d8ab171c80ec8364f7c12e35b23ad 345ecd01c38d18a9036ed96c73b8d066 13056 campinas SP 879864dab9bc3047522c92c82e1212b8 4c93744516667ad3b8f1fb645a3116a4 89254 jaragua do sul SC fd826e7cf63160e536e0908c76c3f441 addec96d2e059c80c30fe6871d30d177 04534 sao paulo SP 5e274e7a0c3809e14aba7ad5aae0d407 57b2a98a409812fe9618067b6b8ebe4f 35182 timoteo MG 5adf08e34b2e993982a47070956c5c65 1175e95fb47ddff9de6b2b06188f7e0d 81560 curitiba PR 4b7139f34592b3a31687243a302fa75b 9afe194fb833f79e300e37e580171f22 30575 belo horizonte MG 9fb35e4ed6f0a14a4977cd9aea4042bb 2a7745e1ed516b289ed9b29c7d0539a5 39400 montes claros MG 5aa9e4fdd4dfd20959cad2d772509598 2a46fb94aef5cbeeb850418118cee090 20231 rio de janeiro RJ b2d1536598b73a9abd18e0d75d92f0a3 918dc87cd72cd9f6ed4bd442ed785235 18682 lencois paulista SP eabebad39a88bb6f5b52376faec28612 295c05e81917928d76245e842748184d 05704 sao paulo SP 1f1c7bf1c9b041b292af6c1c4470b753 3151a81801c8386361b62277d7fa5ecf 95110 caxias do sul RS 206f3129c0e4d7d0b9550426023f0a08 21f748a16f4e1688a9014eb3ee6fa325 13412 piracicaba SP a7c125a0a07b75146167b7f04a7f8e98 5c2991dbd08bbf3cf410713c4de5a0b5 22750 rio de janeiro RJ c5c61596a3b6bd0cee5766992c48a9a1 b6e99561fe6f34a55b0b7da92f8ed775 07124 guarulhos SP 9b8ce803689b3562defaad4613ef426f 7f3a72e8f988c6e735ba118d54f47458 05416 sao paulo SP 49d0ea0986edde72da777f15456a0ee0 3e6fd6b2f0d499456a6a6820a40f2d79 68485 pacaja PA 154c4ded6991bdfa3cd249d11abf4130 e607ede0e63436308660236f5a52da5e 88034 florianopolis SC 690172ab319622688d3b4df42f676898 a96d5cfa0d3181817e2b946f921ea021 74914 aparecida de goiania GO 2938121a40a20953c43caa8c98787fcb 482441ea6a06b1f72fe9784756c0ea75 05713 sao paulo SP 237098a64674ae89babdc426746260fc 4390ddbb6276a66ff1736a6710205dca 82820 curitiba PR cb721d7b4f271fd87011c4c83462c076 a5844ba4bfc8d0cc61d13027c7e63bcc 08225 sao paulo SP f681356046d9fde60e70c73a18d65ea2 5f102dd37243f152aec3607970aad100 09121 santo andre SP 167bd30a409e3e4127df5a9408ebd394 9c0096673baf55453a50073f12d1a37f 74310 goiania GO 6e359a57a91f84095cc64e1b351aef8c 2e6a42a9b5cbb0da62988694f18ee295 04571 sao paulo SP e0eea8f69a457b3f1fa246e44c9ebefd 4d221875624017bc47b4d1ce7314a5b7 29311 cachoeiro de itapemirim ES e3109970a3fe8021d5ff82c577ce5606 a8654e2af5da6bb72f52c22b164855e1 05528 sao paulo SP 261cb4f92498ca05d5bd1a327a261d9c 424aca6872c5bab80780a8dec03b7516 12235 sao jose dos campos SP 6f92779347724b67e44e3224f3b4cffd bf4862777db128507e9efcc789215e9b 18130 sao roque SP 2d5831cb2dff7cdefba62e950ae3dc7b e9dd12dca17352644a959d9dea133935 42800 camacari BA b2bed119388167a954382cca36c4777f e079b18794454de9d2be5c12b4392294 27525 resende RJ 469634941c27cd844170935a3cf60b95 ef07ba9aa5226f77264ffa5762b2280b 81750 curitiba PR df0aa5b8586495e0ddf6b601122e43a1 85d234692f7bee8d6fea586e237334b6 13175 sumare SP 41c8f4b570869791379a925899a6af8a fe3634ccefbcdb0537b45fd589e32e8e 07170 guarulhos SP 54f755c3fd2709231f9964a1430c5218 40febde16f4718a5def537786473b0be 93415 novo hamburgo RS 4c06b42fbf7b97ab10779cda5549cd1c 07d190f123147d9e89d4b922543d7948 65075 sao luis MA b6368ca0f56d4632f44d58ca431487b2 dd992305cba295d997f263dbdf4e8c2e 88104 sao jose SC 4a0e66fd30684aa1409cd1b66fec77cc 86085586aaa8c5f47ed0b400da64c59d 07176 guarulhos SP c168abb9077b7821adae01dc1f0886c5 5ad58a4e6a1a656b6bed070cadbaa003 35960 santa barbara MG a3b0fda37bae14cf754877bed475e80c c9158d089637ab443c78984d20da7fc0 05727 sao paulo SP 0ccd415657ae8a6cd1c71b00155a019e 66cc90195ca44cc7ac6a1cd0e1e1e7b2 07053 guarulhos SP c532a74a3ebf1bacce2e2bcce3783317 91ec50a00ae74d0a229d2efdf4344e1e 14026 ribeirao preto SP 19ce

In [0]:
# Esse join é apenas um exemplo
df_with_customers = customers.join(df, on="customer_id", how="left")

display(df_with_customers)

customer_id customer_unique_id customer_zip_code_prefix customer_city customer_state order_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date order_purchase_year diff_in_days_between_purchase_and_approved e3c7e245a96d7fa339fe6c16f8da4e90 79051ee5ee98c4bd6982e67e2e79dbcb 07847 franco da rocha SP 8d9c47d02bd99ae8d7dd151ededa9281 delivered 2017-10-15 17:12:19 2017-10-15 17:56:24 2017-10-17 21:05:06 2017-10-23 22:04:54 2017-11-01 00:00:00 2017 0 a56b03f5e6015f1a502b9810309b98b7 b6cbe1a8674ee23e9fb086e3c61677b8 41308 salvador BA 4b8f5652792df716a6e936ae0c78a935 delivered 2017-06-26 12:05:33 2017-07-01 21:33:24 2017-06-26 13:05:19 2017-07-12 19:47:28 2017-08-28 00:00:00 2017 5 d0615859a639a94c1fe472eba57d4a7c 9072b46e3b68961565477d90b24092e9 12900 braganca paulista SP d94486278633cac5f50e370851d24de6 delivered 2018-03-15 18:07:49 2018-03-15 18:28:40 2018-03-16 18:55:44 2018-03-19 16:52:07 2018-03-27 00:00:00 2018 0 c0fe0fbc24994167dce810f83cb96890 839bbfd4ff93b592c82a44dcaa9515c3 30330 belo horizonte MG d2adc517116e216add8b6f5b45c3b84e delivered 2017-06-24 13:14:16 2017-06-24 13:25:20 2017-07-11 18:44:44 2017-07-19 18:59:36 2017-08-15 00:00:00 2017 0 5b5f4957a69d537a2aeadfa7dd2d09d9 bb03ed8d9549898e869f0e6774064096 71505 brasilia DF d178d8bdd78765955d2260fc1d639052 delivered 2017-06-23 22:56:47 2017-06-23 23:05:20 2017-06-27 10:33:13 2017-07-06 12:47:40 2017-07-21 00:00:00 2017 0 41b200d1ce8675f154c91c2da887bcee 9b05b38d7d9ef19a89815c217b30fd37 02114 sao paulo SP 9dfd8f2ac479e34a16d68ff827759a23 invoiced 2018-05-15 15:55:01 2018-05-17 02:15:28 null null 2018-06-01 00:00:00 2018 2 456c1e01c8ed3b83aa8fc564119bc81a 4ac6ec83ece04605a854d931c8e8d8c7 59030 natal RN 01b1800f51715ab76f67caf732206437 delivered 2018-07-18 19:05:46 2018-07-18 19:23:14 2018-07-19 09:06:00 2018-07-27 19:26:24 2018-08-08 00:00:00 2018 0 8baeca32aac79a831b81f1f8af9fd6d8 59cd6345c0d1920b6a42f672173a78fd 13950 lindoia SP 1184c1bbcfb488132ee2bca2c07cd743 delivered 2018-08-16 11:35:15 2018-08-16 11:45:09 2018-08-17 08:38:00 2018-08-21 20:07:33 2018-08-27 00:00:00 2018 0 a8004a3d658be3bb26c0ad71671ef73f c1ccdcdeb2daa19091d2aefb8f1a2bd5 05143 sao paulo SP 68e3cd57e173ebad230c2879e6c78401 delivered 2018-04-07 20:56:45 2018-04-10 04:15:40 2018-04-10 20:06:22 2018-04-11 20:48:32 2018-04-19 00:00:00 2018 3 860ac166573be76ffb00c3e483892094 919bf2617845a0f73acc0361cba58267 30535 belo horizonte MG ab77be4cf9bf132ca4d82049e786e528 delivered 2017-09-16 21:10:54 2017-09-19 03:43:56 2017-09-20 16:09:21 2017-09-29 21:27:36 2017-10-06 00:00:00 2017 3 4f8f4d1895013d138194894a1c2905c0 6af7483a320227ed5f3b20b5cea63269 29075 vitoria ES c3897336d5d3d5a54fd2203ee9483312 delivered 2018-06-30 18:37:30 2018-06-30 19:50:05 2018-07-07 09:28:00 2018-07-23 22:58:30 2018-08-03 00:00:00 2018 0 e2431d4ec21d4a66b411af4e65c4cb1b 7a2cb8d19676becd361d051a9684d084 77470 formoso do araguaia TO a523c396a29386423aa594fe448ca713 delivered 2017-11-29 15:49:41 2017-11-29 17:30:55 2017-12-04 20:39:11 2018-01-04 23:48:54 2017-12-28 00:00:00 2017 0 b59bbdb15afd9b563d1347e758f7c599 df46c6acd5853d88f6b5b6fda5eb116e 96020 pelotas RS 271d4e7bb763fdd2d4975ca1421ff1cd delivered 2017-08-26 21:49:01 2017-08-26 22:16:16 2017-08-28 21:24:33 2017-09-01 20:46:28 2017-09-18 00:00:00 2017 0 feedd5ec61cfc3b216599c09345069ce 1322aeab45dddda6c3f9095b167f3afc 78300 tangara da serra MT 513aeb569eda09cb3e7bf6aae2ddcdc4 delivered 2018-07-31 14:39:51 2018-07-31 15:40:13 2018-08-02 11:30:00 2018-08-09 13:38:40 2018-08-20 00:00:00 2018 0 441a64d207dab5faa2b66a381d759148 e30ccb93517415848f88f5d9ea92cd49 22735 rio de janeiro RJ 60f9a8bb9a63c3a3a0a57eedd90f1536 delivered 2018-03-27 15:44:50 2018-03-28 02:50:25 2018-03-28 19:11:04 2018-04-09 20:49:36 2018-05-02 00:00:00 2018 1 5bdebe0bf44ced6aa0ad9a97753e5776 fd7e7e4d74e83f8cdb71feaeb0ab7856 89050 blumenau SC d985fb531fec480414b13531ab8c6e24 delivered 2018-05-09 15:17:02 2018-05-09 15:37:00 201

Lembrando que uma boa prática é sempre selecionar quais colunas vamos utilizar com o método *.select*.

# Window

Outra função extremamente útil é a *Window*. Ela permite criar janelas, particionadas por colunas, para análise dos resultados. Diferentemente do método *.groupby*, que retorna um resultado agregado, o método *Window* retorna um valor (resultado de alguma operação) em todas as linhas do *dataframe*.

No exemplo abaixo vamos utilizar uma janela para determinar a primeira data de compra de cada um dos usuários e coloca-la em uma coluna chama *first_purchase_date*. Esse valor é útil para determinarmos quantos dias uma ordem de compra qualquer demorou para ocorrer em relação a primeira ordem de compra (de determinado usuário).

Outro método para fazer isso envolveria o uso de um método *.groupby* junto com um método *join*.

Esse método é útil para determinarmos coisas como:

- Diferença de tempo (TF - TI) entre eventos;
- Determinação do primeiro evento (ou "n-ésimo") em uma série de eventos;
- Determinção de médias móveis etc.

In [0]:
#Determinando a primeira data de cada ordem para cada customer_unique_id (o resultado será propagado ao longo de todo o dataframe)
window = Window().partitionBy("customer_unique_id")

df_with_customers = df_with_customers.withColumn("first_purchase_date", F.min(F.col("order_purchase_timestamp")).over(window))

display(df_with_customers.select("customer_unique_id", "order_purchase_timestamp", "first_purchase_date"))

customer_unique_id order_purchase_timestamp first_purchase_date 0005e1862207bf6ccc02e4228effd9a0 2017-03-04 23:32:12 2017-03-04 23:32:12 0006fdc98a402fceb4eb0ee528f6a8d4 2017-07-18 09:23:10 2017-07-18 09:23:10 00090324bbad0e9342388303bb71ba0a 2018-03-24 14:44:41 2018-03-24 14:44:41 000c8bdb58a29e7115cfc257230fb21b 2017-12-12 22:53:35 2017-12-12 22:53:35 00115fc7123b5310cf6d3a3aa932699e 2017-01-21 21:58:35 2017-01-21 21:58:35 001a3a8e11d76c9a366c31a4aa2cc529 2018-05-21 01:24:25 2018-05-21 01:24:25 001f3c4211216384d5fe59b041ce1461 2017-03-19 18:34:36 2017-03-19 18:34:36 0023557a94bef0038066b5d1b3dc763e 2018-03-28 19:53:14 2018-03-28 19:53:14 002aba8c1af80acacef6e011f9f23262 2018-02-27 12:47:48 2018-02-27 12:47:48 002b4cd83fabaffaa475f78ea5ef3e08 2017-02-01 13:53:16 2017-02-01 13:53:16 002cdf87d4c03f08f7eb4551a923affc 2017-10-31 17:32:22 2017-10-31 17:32:22 002d71b244beb91ca7030b15ab526446 2017-05-22 22:24:51 2017-05-22 22:24:51 0034c76b7e6a17d738375b99afc2f01e 2018-05-07 16:17:00 2018-05-07 16:17:00 0035029989e6fc5cf030918a5f9f2037 2018-05-12 14:28:16 2018-05-12 14:28:16 0036a074f98b80c4f1fc33dbbcf9c552 2017-05-12 09:24:26 2017-05-12 09:24:26 0036d365b138cc0ee06bed755bcb5044 2018-01-31 14:41:00 2018-01-31 14:41:00 003800162424b7b5b3d75c9cf22a66e7 2018-04-01 21:29:34 2018-04-01 21:29:34 00391594070baf8603f5fdc1d0c6a48c 2018-08-05 20:33:28 2018-08-05 20:33:28 003ae409f37c3c30cb1c974af3a42692 2018-08-15 11:37:45 2018-08-15 11:37:45 004288347e5e88a27ded2bb23747066c 2017-07-27 14:13:03 2017-07-27 14:13:03 004288347e5e88a27ded2bb23747066c 2018-01-14 07:36:54 2017-07-27 14:13:03 0042dfa8925d6eb23e471ec350454f04 2018-07-25 18:33:29 2018-07-25 18:33:29 0048706e497cfba0b689e1e3497bc99e 2018-08-15 16:54:26 2018-08-15 16:54:26 004a432489f6630c6dfd3fc4454603f5 2017-12-16 09:25:10 2017-12-16 09:25:10 004b45ec5c64187465168251cd1c9c2f 2017-09-01 12:11:23 2017-09-01 12:11:23 004b45ec5c64187465168251cd1c9c2f 2018-05-26 19:42:48 2017-09-01 12:11:23 00504b68faa074d0f40adcb4f7727f71 2018-08-11 23:17:37 2018-08-11 23:17:37 0050dcff37f8b9ff611d245e30572b46 2018-05-02 08:44:43 2018-05-02 08:44:43 0056f26cb8f20916c3baa0e39fc30709 2018-03-31 10:38:18 2018-03-31 10:38:18 005754cb59f8ee5cdbb5cda9d138757e 2018-07-21 11:39:34 2018-07-21 11:39:34 005e32bc930906dc6b65fb9d11cce3e2 2017-09-03 21:48:38 2017-09-03 21:48:38 005f060d4223956c62b64e9567a36f0f 2018-05-22 22:36:54 2018-05-22 22:36:54 005ff4ebe100db3eebbe6f7b19a8f99a 2017-09-13 15:10:21 2017-09-13 15:10:21 0063817060d662048ed08bccecaf45d5 2018-01-12 09:26:20 2018-01-12 09:26:20 00651d97d964127ccfc0e2e55464876d 2018-02-26 16:49:57 2018-02-26 16:49:57 006f2f20cf0cd723624b99d0e8e40d0c 2018-02-10 20:45:36 2018-02-10 20:45:36 0074a1d3f1995ff0538dc7197500973c 2018-05-10 11:06:18 2018-05-10 11:06:18 00762eafc5dac5fc1574f91e9b7c9b67 2018-02-07 22:06:31 2018-02-07 22:06:31 00776f3807b128beca64cd0b27138d92 2017-09-21 19:05:52 2017-09-21 19:05:52 0078108af1d2dc4b1601c744ca581b4f 2018-05-07 13:51:40 2018-05-07 13:51:40 0078bb0f0d23e922d08437b7d0e13907 2017-12-21 23:56:54 2017-12-21 23:56:54 007953b3182d5ccc9189a694f5c68163 2017-04-15 22:00:21 2017-04-15 22:00:21 00797f371bc0f6adb4d267be541a92da 2018-04-09 13:43:51 2018-04-09 13:43:51 0079b7407a428543a7f178cc09164035 2017-11-29 17:44:25 2017-11-29 17:44:25 007ba48697b079e78f168b051462dd1b 2018-06-06 23:49:36 2018-06-06 23:49:36 008778a1591d49f6b2464dffaa4fa662 2017-07-19 19:43:14 2017-07-19 19:43:14 0087c31081ea8d160baa06bf4ad4d76f 2018-06-22 19:57:24 2018-06-22 19:57:24 0087eede471173af78d789df249c3a45 2017-02-16 20:12:03 2017-02-16 20:12:03 008b06aba4b5f5b5b94f525ccf520624 2018-08-22 10:49:05 2018-08-22 10:49:05 008b82b072c6b564fcce49a325f84097 2018-03-10 18:42:35 2018-03-10 18:42:35 008ca52811784a181c8c88e8d66b49db 2018-08-15 23:01:42 2018-08-15 23:01:42 00970787f181925ba33bd32b3817f742 2017-09-16 01:30:57 2017-09-16 01:30:57 0097c1e3f3c2fed7a7d8cf30be1a33df 2017-11-27 13:25:08 2017-11-27 13:25:08 0098853a28531d48988a2fb02b30840e 2018-06-08 12:06:19 2018-06-08 12:

## Realizando a mesma operação com groupby

In [0]:
first_purchase_date = df_with_customers.groupby("customer_unique_id").agg(F.min(F.col("order_purchase_timestamp")).alias("first_purchase_date"))

display(df_with_customers.join(first_purchase_date, on="customer_unique_id", how="left").select("customer_unique_id", "order_purchase_timestamp", "first_purchase_date"))

customer_unique_id order_purchase_timestamp first_purchase_date 861eff4711a542e4b93843c6dd7febb0 2017-05-16 15:05:35 2017-05-16 15:05:35 e607ede0e63436308660236f5a52da5e 2017-08-13 10:03:36 2017-08-13 10:03:36 28da048f094c0c9cbbc5412bcf41b6b0 2017-04-04 12:48:23 2017-04-04 12:48:23 212c759d8c4f2d4d9d6fd4c7de0afbb3 2017-09-01 12:05:54 2017-09-01 12:05:54 f96176e892232662d1c1c5896a94e035 2017-08-19 10:08:37 2017-08-19 10:08:37 000c8bdb58a29e7115cfc257230fb21b 2017-12-12 22:53:35 2017-12-12 22:53:35 9ccbb5f759db041b2db8359d71c0547f 2017-12-11 20:03:10 2017-12-11 20:03:10 4b384b778ebc0449d0244902bfce7beb 2017-11-19 14:34:44 2017-06-22 20:05:39 4df43d4c7d3a093a519dbfe0b9dcc0d6 2018-07-08 19:25:52 2018-07-08 19:25:52 4be1583defacacfea129170626a62569 2017-09-22 23:09:49 2017-09-22 23:09:49 c85df1c6ef6f7bb605e1c49d34f172ee 2017-11-05 10:22:05 2017-11-05 10:22:05 1a3d1e8b28c0ee27c23333ee108c47e6 2018-06-28 16:47:41 2018-06-28 16:47:41 2a6ef69674d6f28002c72b8d123b3a27 2018-03-23 16:25:13 2018-03-23 16:25:13 2d6d1699603a346a292ffcaa3a20eb0a 2017-12-29 16:03:43 2017-12-29 16:03:43 5b71ca52f13f79c2be72b2aad8755c0a 2017-08-04 19:12:56 2017-07-29 19:30:58 9a176d6883a469743a27791158707f97 2017-11-16 19:27:48 2017-11-16 19:27:48 dfe634d4b8e0678799178b6ec8e1b0ba 2018-07-15 02:11:15 2018-07-15 02:11:15 5f439c10be261b762af976221efcdbd1 2017-12-04 12:21:45 2017-12-04 12:21:45 cbe71e4cb0b82b97bbec5cd51e0fa3ea 2018-03-04 15:01:18 2018-01-20 00:24:23 782d02110160b9efdd83f0b5d27376ad 2017-07-26 17:37:37 2017-07-26 17:37:37 a86f29fdc92c603fdd3d4f530230644a 2017-09-13 08:10:50 2017-09-13 08:10:50 d84d21b7b4970bdb535a4527ee55ac35 2018-08-12 08:36:16 2018-08-12 08:36:16 c2676cdedacba0e3aed5312e06b9bdda 2017-06-01 16:10:28 2017-06-01 16:10:28 1f66e8e77f5f40caaf63d93909ae7c39 2018-03-26 13:02:11 2018-03-26 13:02:11 05f5af0b8213fa1b6e28e7ed7a47a300 2017-03-28 22:05:00 2017-03-28 22:05:00 f31d2c22ddcad145e224e6dc48f349b9 2018-05-16 20:57:48 2018-04-13 22:12:39 a99697757b492ec1b8cdc2f245d9d116 2018-02-01 21:45:16 2018-02-01 21:45:16 239b3546ef7a0ff14786b56fc026aa68 2017-11-10 13:41:19 2017-11-10 13:41:19 9926adedb498e6c15bdc22ac44560a3b 2017-12-10 09:29:51 2017-12-10 09:29:51 e66c03faee607e9eb86380d0a86a327d 2017-07-13 22:29:41 2017-07-13 22:29:41 38d28c9b9ef86aee5b149ef3b8440500 2018-02-05 19:51:11 2018-02-05 19:51:11 3195d6c23c9f61b0bcfae41d3fe8a3db 2018-06-11 12:48:52 2018-06-11 12:48:52 6916bae3f7ff69e56cb6cfb3c10d5cbb 2017-09-13 16:24:17 2017-09-13 16:24:17 b74836b64aef848ce03435c3f897bfaa 2017-04-25 13:46:24 2017-04-25 13:46:24 14e7273c0d9ae09ddca90384ab4a28e2 2018-04-03 11:05:02 2018-04-03 11:05:02 c2495d0891221237c0146a60af8dd684 2018-01-05 09:43:00 2018-01-05 09:43:00 376c9c37aea85ca26315dfe54b3e4c93 2017-08-27 16:14:04 2017-08-27 16:14:04 a0f1d4ed2825bb48faba637c5a1b4b9b 2017-06-28 22:12:22 2017-06-28 22:12:22 532f7ebebe5e977e5fddcd9f39caa4f2 2018-02-19 11:58:03 2018-02-19 11:58:03 008ca52811784a181c8c88e8d66b49db 2018-08-15 23:01:42 2018-08-15 23:01:42 85b3ae9df63745fe6974a148da9e2191 2017-08-01 13:43:33 2017-08-01 13:43:33 1479fd41a84fd3737d0705434c33f388 2017-07-29 13:50:51 2017-07-29 13:50:51 c2c7712d6c0a2ac5be6a3280042d471b 2017-05-23 13:51:12 2017-05-23 13:51:12 0651e691ed9e201bf2ce26d40f93d739 2017-07-11 15:34:36 2017-07-11 15:34:36 bdee14a4f9d04d3b78a69f7ba1e82425 2018-05-10 18:05:38 2018-05-10 18:05:38 ac28756ae14e9bab4d0da284e2ed0724 2017-09-19 20:03:29 2017-09-19 20:03:29 d242c2a33b19c5fab2ccf4f67dcaba86 2018-05-07 18:56:36 2018-05-07 18:56:36 6ef09a6a7758b108b84fcab47567f3e4 2017-08-10 22:43:08 2017-08-10 22:43:08 28a3ae98731c6bf62767b91aeca1a809 2018-08-09 10:56:48 2018-08-09 10:56:48 8d0e0879191d761df1fde63cd721065d 2018-01-16 15:21:52 2018-01-16 15:21:52 be5f4c2d4e90cdf1051d286f9021b57c 2017-04-28 21:22:30 2017-04-28 21:22:30 16bf924f32df7c2607fac42a6682293c 2017-10-18 20:37:23 2017-10-18 20:37:23 23a886ebce4bc86212c72f669a9bdb31 2018-04-02 20:45:08 2018-04-02 20:45:08 1d5f0643cf2568434743cb9ff674feb3 2018-01-24 12:52:12 2018-01-24 12:

# Mãos a obra

Agora que temos um conhecimento sobre os principais métodos dessa API, vamos aplicá-los para resolvermos alguns problemas de negócio.

## A área de negócio nos fez as seguintes indagações:

1 - Quantidade de ordens agrupadas por ANO/MES/STATUS (eles precisam de um arquivo .CSV contendo todas essas informações);

2 - Quantidade de usuários por estado (para identificarem onde precisam focar os esforços de *marketing*);

3 - Além da quantidade, a área de negócio precisa do *ranking* de cada estado (qual é o primeiro, segundo etc) em termos da quantidade de usuários;

4 - Quantidade de usuários que tiveram mais de três ordens;

5 - Dos usuários que tiveram pelo menos três ordens, quantos dias isso (ter a terceira ordem) levou em relação a primeira ordem de compra;

6 - Qual o recebimento anual médio por tipo de pagamento.

## Devemos saber o seguinte sobre o conjunto de dados:

- *customer_id*: ID do cliente;
- *customer_unique_id*: ID único de cada cliente (esse ID engloba vários *customer_id*);
- *order_purchase_timestamp*: *timestamp* da data da ordem;
- *customer_state*: estado do cliente;
- *payment_type*: tipo de pagamento;

In [0]:
orders = table("orders")
customers = table("customers")
payments = table("payments")

In [0]:
display(orders)

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 53cdb2fc8bc7dce0b6741e2150273451 b0830fb4747a6c6d20dea0b8c802d7ef delivered 2018-07-24 20:41:37 2018-07-26 03:24:27 2018-07-26 14:31:00 2018-08-07 15:27:45 2018-08-13 00:00:00 47770eb9100c2d0c44946d9cf07ec65d 41ce2a54c0b03bf3443c3d931a367089 delivered 2018-08-08 08:38:49 2018-08-08 08:55:23 2018-08-08 13:50:00 2018-08-17 18:06:29 2018-09-04 00:00:00 949d5b44dbf5de918fe9c16f97b45f8a f88197465ea7920adcdbec7375364d82 delivered 2017-11-18 19:28:06 2017-11-18 19:45:59 2017-11-22 13:39:59 2017-12-02 00:28:42 2017-12-15 00:00:00 ad21c59c0840e6cb83a9ceb5573f8159 8ab97904e6daea8866dbdbc4fb7aad2c delivered 2018-02-13 21:18:39 2018-02-13 22:20:29 2018-02-14 19:46:34 2018-02-16 18:17:02 2018-02-26 00:00:00 a4591c265e18cb1dcee52889e2d8acc3 503740e9ca751ccdda7ba28e9ab8f608 delivered 2017-07-09 21:57:05 2017-07-09 22:10:13 2017-07-11 14:58:04 2017-07-26 10:57:55 2017-08-01 00:00:00 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 6514b8ad8028c9f2cc2374ded245783f 9bdf08b4b3b52b5526ff42d37d47f222 delivered 2017-05-16 13:10:30 2017-05-16 13:22:11 2017-05-22 10:07:46 2017-05-26 12:55:51 2017-06-07 00:00:00 76c6e866289321a7c93b82b54852dc33 f54a9f0e6b351c431402b8461ea51999 delivered 2017-01-23 18:29:09 2017-01-25 02:50:47 2017-01-26 14:16:31 2017-02-02 14:08:10 2017-03-06 00:00:00 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 e6ce16cb79ec1d90b1da9085a6118aeb 494dded5b201313c64ed7f100595b95c delivered 2017-05-16 19:41:10 2017-05-16 19:50:18 2017-05-18 11:40:40 2017-05-29 11:18:31 2017-06-07 00:00:00 34513ce0c4fab462a55830c0989c7edb 7711cf624183d843aafe81855097bc37 delivered 2017-07-13 19:58:11 2017-07-13 20:10:08 2017-07-14 18:43:29 2017-07-19 14:04:48 2017-08-08 00:00:00 82566a660a982b15fb86e904c8d32918 d3e3b74c766bc6214e0c830b17ee2341 delivered 2018-06-07 10:06:19 2018-06-09 03:13:12 2018-06-11 13:29:00 2018-06-19 12:05:52 2018-07-18 00:00:00 5ff96c15d0b717ac6ad1f3d77225a350 19402a48fe860416adf93348aba37740 delivered 2018-07-25 17:44:10 2018-07-25 17:55:14 2018-07-26 13:16:00 2018-07-30 15:52:25 2018-08-08 00:00:00 432aaf21d85167c2c86ec9448c4e42cc 3df704f53d3f1d4818840b34ec672a9f delivered 2018-03-01 14:14:28 2018-03-01 15:10:47 2018-03-02 21:09:20 2018-03-12 23:36:26 2018-03-21 00:00:00 dcb36b511fcac050b97cd5c05de84dc3 3b6828a50ffe546942b7a473d70ac0fc delivered 2018-06-07 19:03:12 2018-06-12 23:31:02 2018-06-11 14:54:00 2018-06-21 15:34:32 2018-07-04 00:00:00 403b97836b0c04a622354cf531062e5f 738b086814c6fcc74b8cc583f8516ee3 delivered 2018-01-02 19:00:43 2018-01-02 19:09:04 2018-01-03 18:19:09 2018-01-20 01:38:59 2018-02-06 00:00:00 116f0b09343b49556bbad5f35bee0cdf 3187789bec990987628d7a9beb4dd6ac delivered 2017-12-26 23:41:31 2017-12-26 23:50:22 2017-12-28 18:33:05 2018-01-08 22:36:36 2018-01-29 00:00:00 85ce859fd6dc634de8d2f1e290444043 059f7fc5719c7da6cbafe370971a8d70 delivered 2017-11-21 00:03:41 2017-11-21 00:14:22 2017-11-23 21:32:26 2017-11-27 18:28:00 2017-12-11 00:00:00 83018ec114eee8641c97e08f7b4e926f 7f8c8b9c2ae27bf3300f670c3d478be8 delivered 2017-10-26 15:54:26 2017-10-26 16:08:14 2017-10-26 21:46:53 2017-11-08 22:22:00 2017-11-23 00:00:00 203096f03d82e0dffbc41ebc2e2bcfb7 d2b091571da224a1b36412c18bc3bbfe delivered 2017-09-18 14:31:30 2017-09-19 04:04:09 2017-10-06 17:50:03 2017-10-09 22:23:46 2017-09-28 00:00:00 f848643eec1d69395095eb3840d2051e 4fa1cd166fa598be6de80fa84eaade43 delivered 2018-03-15 08:52:40 2018-03-15 09:09:31 2018-03-15 19:52:48 2018-03-19 18:08:32 2018-03-29 00

In [0]:
display(customers)

customer_id customer_unique_id customer_zip_code_prefix customer_city customer_state 06b8999e2fba1a1fbc88172c00ba8bc7 861eff4711a542e4b93843c6dd7febb0 14409 franca SP 18955e83d337fd6b2def6b18a428ac77 290c77bc529b7ac935b93aa66c333dc3 09790 sao bernardo do campo SP 4e7b3e00288586ebd08712fdd0374a03 060e732b5b29e8181a18229c7b0b2b5e 01151 sao paulo SP b2b6027bc5c5109e529d4dc6358b12c3 259dac757896d24d7702b9acbbff3f3c 08775 mogi das cruzes SP 4f2d8ab171c80ec8364f7c12e35b23ad 345ecd01c38d18a9036ed96c73b8d066 13056 campinas SP 879864dab9bc3047522c92c82e1212b8 4c93744516667ad3b8f1fb645a3116a4 89254 jaragua do sul SC fd826e7cf63160e536e0908c76c3f441 addec96d2e059c80c30fe6871d30d177 04534 sao paulo SP 5e274e7a0c3809e14aba7ad5aae0d407 57b2a98a409812fe9618067b6b8ebe4f 35182 timoteo MG 5adf08e34b2e993982a47070956c5c65 1175e95fb47ddff9de6b2b06188f7e0d 81560 curitiba PR 4b7139f34592b3a31687243a302fa75b 9afe194fb833f79e300e37e580171f22 30575 belo horizonte MG 9fb35e4ed6f0a14a4977cd9aea4042bb 2a7745e1ed516b289ed9b29c7d0539a5 39400 montes claros MG 5aa9e4fdd4dfd20959cad2d772509598 2a46fb94aef5cbeeb850418118cee090 20231 rio de janeiro RJ b2d1536598b73a9abd18e0d75d92f0a3 918dc87cd72cd9f6ed4bd442ed785235 18682 lencois paulista SP eabebad39a88bb6f5b52376faec28612 295c05e81917928d76245e842748184d 05704 sao paulo SP 1f1c7bf1c9b041b292af6c1c4470b753 3151a81801c8386361b62277d7fa5ecf 95110 caxias do sul RS 206f3129c0e4d7d0b9550426023f0a08 21f748a16f4e1688a9014eb3ee6fa325 13412 piracicaba SP a7c125a0a07b75146167b7f04a7f8e98 5c2991dbd08bbf3cf410713c4de5a0b5 22750 rio de janeiro RJ c5c61596a3b6bd0cee5766992c48a9a1 b6e99561fe6f34a55b0b7da92f8ed775 07124 guarulhos SP 9b8ce803689b3562defaad4613ef426f 7f3a72e8f988c6e735ba118d54f47458 05416 sao paulo SP 49d0ea0986edde72da777f15456a0ee0 3e6fd6b2f0d499456a6a6820a40f2d79 68485 pacaja PA 154c4ded6991bdfa3cd249d11abf4130 e607ede0e63436308660236f5a52da5e 88034 florianopolis SC 690172ab319622688d3b4df42f676898 a96d5cfa0d3181817e2b946f921ea021 74914 aparecida de goiania GO 2938121a40a20953c43caa8c98787fcb 482441ea6a06b1f72fe9784756c0ea75 05713 sao paulo SP 237098a64674ae89babdc426746260fc 4390ddbb6276a66ff1736a6710205dca 82820 curitiba PR cb721d7b4f271fd87011c4c83462c076 a5844ba4bfc8d0cc61d13027c7e63bcc 08225 sao paulo SP f681356046d9fde60e70c73a18d65ea2 5f102dd37243f152aec3607970aad100 09121 santo andre SP 167bd30a409e3e4127df5a9408ebd394 9c0096673baf55453a50073f12d1a37f 74310 goiania GO 6e359a57a91f84095cc64e1b351aef8c 2e6a42a9b5cbb0da62988694f18ee295 04571 sao paulo SP e0eea8f69a457b3f1fa246e44c9ebefd 4d221875624017bc47b4d1ce7314a5b7 29311 cachoeiro de itapemirim ES e3109970a3fe8021d5ff82c577ce5606 a8654e2af5da6bb72f52c22b164855e1 05528 sao paulo SP 261cb4f92498ca05d5bd1a327a261d9c 424aca6872c5bab80780a8dec03b7516 12235 sao jose dos campos SP 6f92779347724b67e44e3224f3b4cffd bf4862777db128507e9efcc789215e9b 18130 sao roque SP 2d5831cb2dff7cdefba62e950ae3dc7b e9dd12dca17352644a959d9dea133935 42800 camacari BA b2bed119388167a954382cca36c4777f e079b18794454de9d2be5c12b4392294 27525 resende RJ 469634941c27cd844170935a3cf60b95 ef07ba9aa5226f77264ffa5762b2280b 81750 curitiba PR df0aa5b8586495e0ddf6b601122e43a1 85d234692f7bee8d6fea586e237334b6 13175 sumare SP 41c8f4b570869791379a925899a6af8a fe3634ccefbcdb0537b45fd589e32e8e 07170 guarulhos SP 54f755c3fd2709231f9964a1430c5218 40febde16f4718a5def537786473b0be 93415 novo hamburgo RS 4c06b42fbf7b97ab10779cda5549cd1c 07d190f123147d9e89d4b922543d7948 65075 sao luis MA b6368ca0f56d4632f44d58ca431487b2 dd992305cba295d997f263dbdf4e8c2e 88104 sao jose SC 4a0e66fd30684aa1409cd1b66fec77cc 86085586aaa8c5f47ed0b400da64c59d 07176 guarulhos SP c168abb9077b7821adae01dc1f0886c5 5ad58a4e6a1a656b6bed070cadbaa003 35960 santa barbara MG a3b0fda37bae14cf754877bed475e80c c9158d089637ab443c78984d20da7fc0 05727 sao paulo SP 0ccd415657ae8a6cd1c71b00155a019e 66cc90195ca44cc7ac6a1cd0e1e1e7b2 07053 guarulhos SP c532a74a3ebf1bacce2e2bcce3783317 91ec50a00ae74d0a229d2efdf4344e1e 14026 ribeirao preto SP 19ce

In [0]:
display(payments)

order_id payment_sequential payment_type payment_installments payment_value b81ef226f3fe1789b1e8b2acac839d17 1 credit_card 8 99.33 a9810da82917af2d9aefd1278f1dcfa0 1 credit_card 1 24.39 25e8ea4e93396b6fa0d3dd708e76c1bd 1 credit_card 1 65.71 ba78997921bbcdc1373bb41e913ab953 1 credit_card 8 107.78 42fdf880ba16b47b59251dd489d4441a 1 credit_card 2 128.45 298fcdf1f73eb413e4d26d01b25bc1cd 1 credit_card 2 96.12 771ee386b001f06208a7419e4fc1bbd7 1 credit_card 1 81.16 3d7239c394a212faae122962df514ac7 1 credit_card 3 51.84 1f78449c87a54faf9e96e88ba1491fa9 1 credit_card 6 341.09 0573b5e23cbd798006520e1d5b4c6714 1 boleto 1 51.95 d88e0d5fa41661ce03cf6cf336527646 1 credit_card 8 188.73 2480f727e869fdeb397244a21b721b67 1 credit_card 1 141.90 616105c9352a9668c38303ad44e056cd 1 credit_card 1 75.78 cf95215a722f3ebf29e6bbab87a29e61 1 credit_card 5 102.66 769214176682788a92801d8907fa1b40 1 credit_card 4 105.28 12e5cfe0e4716b59afb0e0f4a3bd6570 1 credit_card 10 157.45 61059985a6fc0ad64e95d9944caacdad 1 credit_card 1 132.04 79da3f5fe31ad1e454f06f95dc032ad5 1 credit_card 1 98.94 8ac09207f415d55acff302df7d6a895c 1 credit_card 4 244.15 b2349a3f20dfbeef62e7b31baa22f84b 1 credit_card 3 136.71 5a1f6d22f7dfb061ef29216b9af687a1 1 credit_card 4 47.69 4214cda550ece8ee66441f459dc33a8c 1 credit_card 2 170.57 adfbf6c2a620196f9a3ec747491c72b7 1 credit_card 4 67.50 4d680edbaa7d3d9bed69532957368a03 1 credit_card 10 353.09 8cd68144cdb62dc0d60848cf8616d2a4 1 boleto 1 330.66 5cfd514482e22bc992e7693f0e3e8df7 2 voucher 1 45.17 d0a945f85ba1074b60aac97ade7e240e 1 credit_card 2 541.00 c39414c195d0f94c9d9c35e7c6ed4f1a 1 credit_card 2 139.22 5d9c5817e278892b7498d90bfa28ade8 1 credit_card 2 290.16 b69b9260e79a0da00e15f48de1bd2524 1 boleto 1 283.34 f45074ae38f2e01d9b854ec8d40362ff 1 credit_card 1 13.78 81cedc4d2132eb6f512354166e51b187 1 credit_card 1 30.28 595f598849d89203c28d05d0fbf3f92e 1 credit_card 1 26.58 f9d0ec2fa088ac583e1ccd15b6686073 1 credit_card 1 89.68 e647bf617de735448a4ba54f8910393c 1 credit_card 1 65.09 b2bb080b6bc860118a246fd9b6fad6da 1 credit_card 1 173.84 23f10f509600c30cf2852f9dbdf28fc3 1 credit_card 1 103.49 f86f6472fa9f395d8d9a6751ca118afb 1 credit_card 1 64.03 1dcf0c8cd36ffaf57784fbdc90079310 1 credit_card 3 157.15 00d8d65b666158b633f96054d31af43b 1 boleto 1 130.88 cf30fe76d1505192acee1c6dccb15545 1 credit_card 2 47.72 d3e774a185c0b1b2286ffd6c70abe2e6 1 credit_card 8 117.74 32b1d8f3789a57f1f752e20ac7404b4c 1 boleto 1 56.60 c10d412026c4077b8e83acf0fea04eee 1 credit_card 1 266.16 56c3277583e16009c925fdf116df420f 1 boleto 1 31.38 0e0441786430b7cfcd0d91f822ea4c99 1 credit_card 1 121.49 6ffb3f1686bceae3466facf7e02ce3fb 1 credit_card 1 32.00 afef48d3c8a0b1b7c9b7f8f922fb5674 1 credit_card 5 153.41 c0db7d31ace61fc360a3eaa34dd3457c 1 credit_card 5 65.71 d574338f566ca28dd67820f48ec1f1d8 1 credit_card 4 278.22 1807cc736321f14baa58ef39cf6e5989 1 credit_card 4 91.66 e8977f709bbb0367f51b589e6325f991 1 credit_card 1 132.51 2e2c60b99754ae1e4d8b18846cfec9f2 1 credit_card 4 542.66 1ffb3c1929b16d9c1aec1958e11b3e9b 1 boleto 1 166.04 95442deb81a5d91c97c0df96b431634a 1 boleto 1 368.98 10af96a0689260134307879127ac1952 1 credit_card 2 113.20 85eef2d342b0de363c45c1bc324729c5 1 credit_card 3 99.43 aa964845f1de8125410aea8b73e9e1ec 1 credit_card 2 27.35 343348b1e29e9fa9e7b6ab1027f9177d 1 credit_card 4 43.77 ad4098a257676ea4d394fb3bbbf36ca3 1 credit_card 2 68.49 3e0c3cab458e8b3cc8d1d38ecb7e7775 1 credit_card 2 105.53 3ab4eea6776259ae8dfbabaeffece352 1 credit_card 8 387.80 10d9871bed9fb8d0887d3b9022edd1ff 1 boleto 1 84.14 c108072ab31ec90a754129c171577f5f 1 credit_card 4 210.82 fc662bafa52d2ef16078f6f6141009d6 1 boleto 1 90.05 4217849b1ff18a9270fe048eabc4dc45 1 credit_card 1 67.88 795c16acb4e3c30dfa5b6827727ef488 1 credit_card 2 37.58 55e2d723733c45033e71cb4d44690234 1 boleto 1 89.63 947e9c6bfd83a06953c420ef92d3da6e 1 voucher 1 69.46 60e43c5f5ba559d9dd19357ed72cb2f2 1 credit_card 2 78.30 e3e9e3295f4e1512167c232a0aaae8a5 1 voucher 1 50.80 460d57443ffdcaeba240360239747cf7 1 credit_card 1 

### Primeira pergunta: Quantidade de ordens agrupadas por ANO/MES/STATUS (eles precisam de um arquivo .CSV contendo todas essas informações)

In [0]:
answer_1 = orders.groupby(F.date_format(F.col("order_purchase_timestamp"), format="y-M").alias("year_month"), "order_status").count()
display(answer_1)

year_month order_status count 2017-3 delivered 2546 2018-6 delivered 6099 2017-6 delivered 3135 2017-12 canceled 11 2017-5 canceled 29 2017-8 processing 18 2018-6 canceled 18 2017-12 shipped 57 2017-9 unavailable 38 2018-8 invoiced 23 2016-10 canceled 24 2017-7 invoiced 7 2016-10 invoiced 18 2018-5 shipped 54 2017-7 canceled 28 2018-8 canceled 84 2018-6 unavailable 4 2018-1 unavailable 48 2018-7 canceled 41 2018-3 processing 9 2017-1 invoiced 12 2016-9 shipped 1 2017-8 unavailable 32 2018-8 delivered 6351 2017-10 unavailable 58 2017-2 canceled 17 2018-5 processing 6 2017-1 unavailable 10 2017-8 canceled 27 2017-3 canceled 33 2018-3 invoiced 23 2017-4 invoiced 14 2017-3 processing 23 2017-10 canceled 26 2017-11 created 2 2017-3 unavailable 32 2017-5 processing 23 2018-4 delivered 6798 2018-6 shipped 43 2017-10 processing 20 2018-2 unavailable 30 2018-7 delivered 6159 2017-1 shipped 16 2017-1 processing 9 2017-6 invoiced 11 2017-5 invoiced 16 2018-3 unavailable 17 2016-10 shipped 8 2018-4 unavailable 5 2017-11 invoiced 35 2017-6 canceled 16 2017-6 shipped 47 2017-11 processing 25 2017-4 canceled 18 2017-4 delivered 2303 2018-3 delivered 7003 2017-7 processing 11 2017-8 shipped 41 2017-8 delivered 4193 2017-7 delivered 3872 2018-9 canceled 15 2017-2 unavailable 45 2017-1 canceled 3 2018-1 canceled 34 2017-2 delivered 1653 2017-1 delivered 750 2018-2 shipped 57 2017-5 unavailable 31 2018-1 delivered 7069 2017-10 invoiced 16 2017-10 delivered 4478 2018-1 shipped 74 2017-11 shipped 72 2017-5 delivered 3546 2018-4 processing 8 2017-3 shipped 45 2017-9 delivered 4150 2018-4 invoiced 14 2018-4 shipped 99 2017-12 processing 35 2017-2 shipped 21 2018-7 shipped 60 2017-4 processing 10 2018-8 shipped 47 2016-10 processing 2 2017-5 shipped 55 2017-11 canceled 37 2018-4 canceled 15 2017-7 shipped 56 2017-8 invoiced 20 2018-2 created 1 2017-12 delivered 5513 2017-9 shipped 38 2018-1 invoiced 15 2017-9 canceled 20 2017-9 processing 22 2018-1 processing 29 2017-12 unavailable 42 2017-2 processing 32 2017-6 unavailable 24 2017-9 invoiced 17 2018-5 invoiced 24 2018-7 invoiced 13 2017-10 shipped 33 2018-5 delivered 6749 2018-2 canceled 73 2018-5 canceled 24 2017-2 invoiced 11 2017-4 shipped 49 2017-11 unavailable 84 2018-8 unavailable 7 2016-9 canceled 2 2017-12 created 2 2018-3 shipped 133 2018-5 unavailable 16 2017-12 invoiced 13 2018-3 canceled 26 2018-7 unavailable 18 2018-2 invoiced 6 2018-2 processing 6 2017-11 delivered 7289 2017-7 unavailable 52 2018-2 delivered 6555 2016-10 delivered 265 2016-12 delivered 1 2017-3 invoiced 3 2016-10 unavailable 7 2017-6 processing 12 2018-10 canceled 4 2017-2 approved 1 2017-4 unavailable 9 2016-9 delivered 1 2018-9 shipped 1 2018-6 invoiced 3 2018-7 processing 1 2017-4 approved 1

In [0]:
#repartition é utilizado para salvarmos apenas um arquivo (por padrão os arquivos são particionados, então vários pedaços são gerado após um write, esse é um tópico mais avançado, que requer um material especial sobre)
answer_1.repartition(1).write.csv("/FileStore/tables/answer_1")

### Segunda pergunta: Quantidade de clientes por estado (para identificarem onde precisam focar os esforços de marketing)

In [0]:
display(customers)

customer_id customer_unique_id customer_zip_code_prefix customer_city customer_state 06b8999e2fba1a1fbc88172c00ba8bc7 861eff4711a542e4b93843c6dd7febb0 14409 franca SP 18955e83d337fd6b2def6b18a428ac77 290c77bc529b7ac935b93aa66c333dc3 09790 sao bernardo do campo SP 4e7b3e00288586ebd08712fdd0374a03 060e732b5b29e8181a18229c7b0b2b5e 01151 sao paulo SP b2b6027bc5c5109e529d4dc6358b12c3 259dac757896d24d7702b9acbbff3f3c 08775 mogi das cruzes SP 4f2d8ab171c80ec8364f7c12e35b23ad 345ecd01c38d18a9036ed96c73b8d066 13056 campinas SP 879864dab9bc3047522c92c82e1212b8 4c93744516667ad3b8f1fb645a3116a4 89254 jaragua do sul SC fd826e7cf63160e536e0908c76c3f441 addec96d2e059c80c30fe6871d30d177 04534 sao paulo SP 5e274e7a0c3809e14aba7ad5aae0d407 57b2a98a409812fe9618067b6b8ebe4f 35182 timoteo MG 5adf08e34b2e993982a47070956c5c65 1175e95fb47ddff9de6b2b06188f7e0d 81560 curitiba PR 4b7139f34592b3a31687243a302fa75b 9afe194fb833f79e300e37e580171f22 30575 belo horizonte MG 9fb35e4ed6f0a14a4977cd9aea4042bb 2a7745e1ed516b289ed9b29c7d0539a5 39400 montes claros MG 5aa9e4fdd4dfd20959cad2d772509598 2a46fb94aef5cbeeb850418118cee090 20231 rio de janeiro RJ b2d1536598b73a9abd18e0d75d92f0a3 918dc87cd72cd9f6ed4bd442ed785235 18682 lencois paulista SP eabebad39a88bb6f5b52376faec28612 295c05e81917928d76245e842748184d 05704 sao paulo SP 1f1c7bf1c9b041b292af6c1c4470b753 3151a81801c8386361b62277d7fa5ecf 95110 caxias do sul RS 206f3129c0e4d7d0b9550426023f0a08 21f748a16f4e1688a9014eb3ee6fa325 13412 piracicaba SP a7c125a0a07b75146167b7f04a7f8e98 5c2991dbd08bbf3cf410713c4de5a0b5 22750 rio de janeiro RJ c5c61596a3b6bd0cee5766992c48a9a1 b6e99561fe6f34a55b0b7da92f8ed775 07124 guarulhos SP 9b8ce803689b3562defaad4613ef426f 7f3a72e8f988c6e735ba118d54f47458 05416 sao paulo SP 49d0ea0986edde72da777f15456a0ee0 3e6fd6b2f0d499456a6a6820a40f2d79 68485 pacaja PA 154c4ded6991bdfa3cd249d11abf4130 e607ede0e63436308660236f5a52da5e 88034 florianopolis SC 690172ab319622688d3b4df42f676898 a96d5cfa0d3181817e2b946f921ea021 74914 aparecida de goiania GO 2938121a40a20953c43caa8c98787fcb 482441ea6a06b1f72fe9784756c0ea75 05713 sao paulo SP 237098a64674ae89babdc426746260fc 4390ddbb6276a66ff1736a6710205dca 82820 curitiba PR cb721d7b4f271fd87011c4c83462c076 a5844ba4bfc8d0cc61d13027c7e63bcc 08225 sao paulo SP f681356046d9fde60e70c73a18d65ea2 5f102dd37243f152aec3607970aad100 09121 santo andre SP 167bd30a409e3e4127df5a9408ebd394 9c0096673baf55453a50073f12d1a37f 74310 goiania GO 6e359a57a91f84095cc64e1b351aef8c 2e6a42a9b5cbb0da62988694f18ee295 04571 sao paulo SP e0eea8f69a457b3f1fa246e44c9ebefd 4d221875624017bc47b4d1ce7314a5b7 29311 cachoeiro de itapemirim ES e3109970a3fe8021d5ff82c577ce5606 a8654e2af5da6bb72f52c22b164855e1 05528 sao paulo SP 261cb4f92498ca05d5bd1a327a261d9c 424aca6872c5bab80780a8dec03b7516 12235 sao jose dos campos SP 6f92779347724b67e44e3224f3b4cffd bf4862777db128507e9efcc789215e9b 18130 sao roque SP 2d5831cb2dff7cdefba62e950ae3dc7b e9dd12dca17352644a959d9dea133935 42800 camacari BA b2bed119388167a954382cca36c4777f e079b18794454de9d2be5c12b4392294 27525 resende RJ 469634941c27cd844170935a3cf60b95 ef07ba9aa5226f77264ffa5762b2280b 81750 curitiba PR df0aa5b8586495e0ddf6b601122e43a1 85d234692f7bee8d6fea586e237334b6 13175 sumare SP 41c8f4b570869791379a925899a6af8a fe3634ccefbcdb0537b45fd589e32e8e 07170 guarulhos SP 54f755c3fd2709231f9964a1430c5218 40febde16f4718a5def537786473b0be 93415 novo hamburgo RS 4c06b42fbf7b97ab10779cda5549cd1c 07d190f123147d9e89d4b922543d7948 65075 sao luis MA b6368ca0f56d4632f44d58ca431487b2 dd992305cba295d997f263dbdf4e8c2e 88104 sao jose SC 4a0e66fd30684aa1409cd1b66fec77cc 86085586aaa8c5f47ed0b400da64c59d 07176 guarulhos SP c168abb9077b7821adae01dc1f0886c5 5ad58a4e6a1a656b6bed070cadbaa003 35960 santa barbara MG a3b0fda37bae14cf754877bed475e80c c9158d089637ab443c78984d20da7fc0 05727 sao paulo SP 0ccd415657ae8a6cd1c71b00155a019e 66cc90195ca44cc7ac6a1cd0e1e1e7b2 07053 guarulhos SP c532a74a3ebf1bacce2e2bcce3783317 91ec50a00ae74d0a229d2efdf4344e1e 14026 ribeirao preto SP 19ce

In [0]:
answer_2 = customers.groupby("customer_state").count()
display(answer_2)

customer_state count SC 3637 RO 253 PI 495 AM 148 RR 46 GO 2020 TO 280 MT 907 SP 41746 ES 2033 PB 536 RS 5466 MS 715 AL 413 MG 11635 PA 975 BA 3380 SE 350 PE 1652 CE 1336 RN 485 RJ 12852 MA 747 AC 81 DF 2140 PR 5045 AP 68

### Terceira pergunta: Além da quantidade, a área de negócio precisa do ranking de cada estado (qual é o primeiro, segundo etc)

In [0]:
#Vamos utilizar os dados da resposta anterior

#Precisamos definir uma janela (sem partição, o que significa que essa janela é a nossa bases de dados inteira) e ordená-la do maior para o menor
window = Window().orderBy(F.col("count").desc())
#Após isso vamos aplicar a operação F.rank() sobre essa janela
answer_3 = answer_2.withColumn("rank", F.rank().over(window))

display(answer_3)

customer_state count rank SP 41746 1 RJ 12852 2 MG 11635 3 RS 5466 4 PR 5045 5 SC 3637 6 BA 3380 7 DF 2140 8 ES 2033 9 GO 2020 10 PE 1652 11 CE 1336 12 PA 975 13 MT 907 14 MA 747 15 MS 715 16 PB 536 17 PI 495 18 RN 485 19 AL 413 20 SE 350 21 TO 280 22 RO 253 23 AM 148 24 AC 81 25 AP 68 26 RR 46 27

### Quarta pergunta: Quantidade de usuários que tiveram mais de três ordens

In [0]:
display(orders)

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 53cdb2fc8bc7dce0b6741e2150273451 b0830fb4747a6c6d20dea0b8c802d7ef delivered 2018-07-24 20:41:37 2018-07-26 03:24:27 2018-07-26 14:31:00 2018-08-07 15:27:45 2018-08-13 00:00:00 47770eb9100c2d0c44946d9cf07ec65d 41ce2a54c0b03bf3443c3d931a367089 delivered 2018-08-08 08:38:49 2018-08-08 08:55:23 2018-08-08 13:50:00 2018-08-17 18:06:29 2018-09-04 00:00:00 949d5b44dbf5de918fe9c16f97b45f8a f88197465ea7920adcdbec7375364d82 delivered 2017-11-18 19:28:06 2017-11-18 19:45:59 2017-11-22 13:39:59 2017-12-02 00:28:42 2017-12-15 00:00:00 ad21c59c0840e6cb83a9ceb5573f8159 8ab97904e6daea8866dbdbc4fb7aad2c delivered 2018-02-13 21:18:39 2018-02-13 22:20:29 2018-02-14 19:46:34 2018-02-16 18:17:02 2018-02-26 00:00:00 a4591c265e18cb1dcee52889e2d8acc3 503740e9ca751ccdda7ba28e9ab8f608 delivered 2017-07-09 21:57:05 2017-07-09 22:10:13 2017-07-11 14:58:04 2017-07-26 10:57:55 2017-08-01 00:00:00 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 6514b8ad8028c9f2cc2374ded245783f 9bdf08b4b3b52b5526ff42d37d47f222 delivered 2017-05-16 13:10:30 2017-05-16 13:22:11 2017-05-22 10:07:46 2017-05-26 12:55:51 2017-06-07 00:00:00 76c6e866289321a7c93b82b54852dc33 f54a9f0e6b351c431402b8461ea51999 delivered 2017-01-23 18:29:09 2017-01-25 02:50:47 2017-01-26 14:16:31 2017-02-02 14:08:10 2017-03-06 00:00:00 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 e6ce16cb79ec1d90b1da9085a6118aeb 494dded5b201313c64ed7f100595b95c delivered 2017-05-16 19:41:10 2017-05-16 19:50:18 2017-05-18 11:40:40 2017-05-29 11:18:31 2017-06-07 00:00:00 34513ce0c4fab462a55830c0989c7edb 7711cf624183d843aafe81855097bc37 delivered 2017-07-13 19:58:11 2017-07-13 20:10:08 2017-07-14 18:43:29 2017-07-19 14:04:48 2017-08-08 00:00:00 82566a660a982b15fb86e904c8d32918 d3e3b74c766bc6214e0c830b17ee2341 delivered 2018-06-07 10:06:19 2018-06-09 03:13:12 2018-06-11 13:29:00 2018-06-19 12:05:52 2018-07-18 00:00:00 5ff96c15d0b717ac6ad1f3d77225a350 19402a48fe860416adf93348aba37740 delivered 2018-07-25 17:44:10 2018-07-25 17:55:14 2018-07-26 13:16:00 2018-07-30 15:52:25 2018-08-08 00:00:00 432aaf21d85167c2c86ec9448c4e42cc 3df704f53d3f1d4818840b34ec672a9f delivered 2018-03-01 14:14:28 2018-03-01 15:10:47 2018-03-02 21:09:20 2018-03-12 23:36:26 2018-03-21 00:00:00 dcb36b511fcac050b97cd5c05de84dc3 3b6828a50ffe546942b7a473d70ac0fc delivered 2018-06-07 19:03:12 2018-06-12 23:31:02 2018-06-11 14:54:00 2018-06-21 15:34:32 2018-07-04 00:00:00 403b97836b0c04a622354cf531062e5f 738b086814c6fcc74b8cc583f8516ee3 delivered 2018-01-02 19:00:43 2018-01-02 19:09:04 2018-01-03 18:19:09 2018-01-20 01:38:59 2018-02-06 00:00:00 116f0b09343b49556bbad5f35bee0cdf 3187789bec990987628d7a9beb4dd6ac delivered 2017-12-26 23:41:31 2017-12-26 23:50:22 2017-12-28 18:33:05 2018-01-08 22:36:36 2018-01-29 00:00:00 85ce859fd6dc634de8d2f1e290444043 059f7fc5719c7da6cbafe370971a8d70 delivered 2017-11-21 00:03:41 2017-11-21 00:14:22 2017-11-23 21:32:26 2017-11-27 18:28:00 2017-12-11 00:00:00 83018ec114eee8641c97e08f7b4e926f 7f8c8b9c2ae27bf3300f670c3d478be8 delivered 2017-10-26 15:54:26 2017-10-26 16:08:14 2017-10-26 21:46:53 2017-11-08 22:22:00 2017-11-23 00:00:00 203096f03d82e0dffbc41ebc2e2bcfb7 d2b091571da224a1b36412c18bc3bbfe delivered 2017-09-18 14:31:30 2017-09-19 04:04:09 2017-10-06 17:50:03 2017-10-09 22:23:46 2017-09-28 00:00:00 f848643eec1d69395095eb3840d2051e 4fa1cd166fa598be6de80fa84eaade43 delivered 2018-03-15 08:52:40 2018-03-15 09:09:31 2018-03-15 19:52:48 2018-03-19 18:08:32 2018-03-29 00

In [0]:
orders_with_customers = orders.join(customers, on="customer_id", how="left")

display(orders_with_customers)

customer_id order_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date customer_unique_id customer_zip_code_prefix customer_city customer_state 9ef432eb6251297304e76186b10a928d e481f51cbdc54678b7cc49136f2d6af7 delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 7c396fd4830fd04220f754e42b4e5bff 03149 sao paulo SP b0830fb4747a6c6d20dea0b8c802d7ef 53cdb2fc8bc7dce0b6741e2150273451 delivered 2018-07-24 20:41:37 2018-07-26 03:24:27 2018-07-26 14:31:00 2018-08-07 15:27:45 2018-08-13 00:00:00 af07308b275d755c9edb36a90c618231 47813 barreiras BA 41ce2a54c0b03bf3443c3d931a367089 47770eb9100c2d0c44946d9cf07ec65d delivered 2018-08-08 08:38:49 2018-08-08 08:55:23 2018-08-08 13:50:00 2018-08-17 18:06:29 2018-09-04 00:00:00 3a653a41f6f9fc3d2a113cf8398680e8 75265 vianopolis GO f88197465ea7920adcdbec7375364d82 949d5b44dbf5de918fe9c16f97b45f8a delivered 2017-11-18 19:28:06 2017-11-18 19:45:59 2017-11-22 13:39:59 2017-12-02 00:28:42 2017-12-15 00:00:00 7c142cf63193a1473d2e66489a9ae977 59296 sao goncalo do amarante RN 8ab97904e6daea8866dbdbc4fb7aad2c ad21c59c0840e6cb83a9ceb5573f8159 delivered 2018-02-13 21:18:39 2018-02-13 22:20:29 2018-02-14 19:46:34 2018-02-16 18:17:02 2018-02-26 00:00:00 72632f0f9dd73dfee390c9b22eb56dd6 09195 santo andre SP 503740e9ca751ccdda7ba28e9ab8f608 a4591c265e18cb1dcee52889e2d8acc3 delivered 2017-07-09 21:57:05 2017-07-09 22:10:13 2017-07-11 14:58:04 2017-07-26 10:57:55 2017-08-01 00:00:00 80bb27c7c16e8f973207a5086ab329e2 86320 congonhinhas PR ed0271e0b7da060a393796590e7b737a 136cce7faa42fdb2cefd53fdc79a6098 invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 36edbb3fb164b1f16485364b6fb04c73 98900 santa rosa RS 9bdf08b4b3b52b5526ff42d37d47f222 6514b8ad8028c9f2cc2374ded245783f delivered 2017-05-16 13:10:30 2017-05-16 13:22:11 2017-05-22 10:07:46 2017-05-26 12:55:51 2017-06-07 00:00:00 932afa1e708222e5821dac9cd5db4cae 26525 nilopolis RJ f54a9f0e6b351c431402b8461ea51999 76c6e866289321a7c93b82b54852dc33 delivered 2017-01-23 18:29:09 2017-01-25 02:50:47 2017-01-26 14:16:31 2017-02-02 14:08:10 2017-03-06 00:00:00 39382392765b6dc74812866ee5ee92a7 99655 faxinalzinho RS 31ad1d1b63eb9962463f764d4e6e0c9d e69bfb5eb88e0ed6a785585b27e16dbf delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 299905e3934e9e181bfb2e164dd4b4f8 18075 sorocaba SP 494dded5b201313c64ed7f100595b95c e6ce16cb79ec1d90b1da9085a6118aeb delivered 2017-05-16 19:41:10 2017-05-16 19:50:18 2017-05-18 11:40:40 2017-05-29 11:18:31 2017-06-07 00:00:00 f2a85dec752b8517b5e58a06ff3cd937 20780 rio de janeiro RJ 7711cf624183d843aafe81855097bc37 34513ce0c4fab462a55830c0989c7edb delivered 2017-07-13 19:58:11 2017-07-13 20:10:08 2017-07-14 18:43:29 2017-07-19 14:04:48 2017-08-08 00:00:00 782987b81c92239d922aa49d6bd4200b 04278 sao paulo SP d3e3b74c766bc6214e0c830b17ee2341 82566a660a982b15fb86e904c8d32918 delivered 2018-06-07 10:06:19 2018-06-09 03:13:12 2018-06-11 13:29:00 2018-06-19 12:05:52 2018-07-18 00:00:00 e97109680b052ee858d93a539597bba7 35400 ouro preto MG 19402a48fe860416adf93348aba37740 5ff96c15d0b717ac6ad1f3d77225a350 delivered 2018-07-25 17:44:10 2018-07-25 17:55:14 2018-07-26 13:16:00 2018-07-30 15:52:25 2018-08-08 00:00:00 e2dfa3127fedbbca9707b36304996dab 04812 sao paulo SP 3df704f53d3f1d4818840b34ec672a9f 432aaf21d85167c2c86ec9448c4e42cc delivered 2018-03-01 14:14:28 2018-03-01 15:10:47 2018-03-02 21:09:20 2018-03-12 23:36:26 2018-03-21 00:00:00 04cf8185c71090d28baa4407b2e6d600 05271 sao paulo SP 3b6828a50ffe546942b7a473d70ac0fc dcb36b511fcac050b97cd5c05de84dc3 delivered 2018-06-07 19:03:12 2018-06-12 23:31:02 2018-06-11 14:54:00 2018-06-21 15:34:32 2018-07-04 00:00:00 ccafc1c3f270410521c3c6f3b249870f 74820 goiania GO 738b086814c6fcc74b8cc583f8516ee3 403b97836b0c04a622354cf531062e5f delivered 2018-01-02 19:00:43 2018-01-02 19:09:04 2

In [0]:
#Encadeando operações
answer_4 = (orders_with_customers
            .groupby("customer_unique_id").count()
            .filter(F.col("count") >= 3)
           )

print(f"Quantidade de clientes: {answer_4.count()}.")

Quantidade de clientes: 252.


### Quinta pergunta: Dos usuários que tiveram pelo menos três ordens, quantos dias isso (ter a terceira ordem) levou em relação a primeira ordem de compra

In [0]:
window = Window().partitionBy("customer_unique_id").orderBy(F.col("order_purchase_timestamp"))

#Definindo a primeira data de compra de cada cliente
answer_5 = (orders_with_customers
            .withColumn("first_order_purchase_timestamp", 
                        F.first(F.col("order_purchase_timestamp")).over(window))
            .withColumn("order_rank", F.row_number().over(window))
            .filter(F.col("order_rank") == 3)
            .withColumn("date_diff", F.datediff(F.col("order_purchase_timestamp"), F.col("first_order_purchase_timestamp")))
            .select("customer_unique_id", "order_purchase_timestamp", "first_order_purchase_timestamp", "date_diff")
           )

display(answer_5)

customer_unique_id order_purchase_timestamp first_order_purchase_timestamp date_diff 0e4cb268bd62da7db135af6349b4fc2a 2017-11-24 20:39:01 2017-11-24 13:15:25 0 182053495bc94c2f41090ce8c41be266 2018-08-19 12:58:22 2018-04-11 14:58:15 130 1da09dd64e235e7c2f29a4faff33535c 2018-01-11 11:16:49 2017-05-10 14:04:15 246 2e43e031f10de28e557c35ef668f9396 2017-01-26 13:15:42 2017-01-26 13:15:41 0 310647380793836bfa5b7b6b3f518423 2017-10-18 13:34:48 2017-04-18 09:46:40 183 320e13a9e22b4e4cda8c17ed1c140ce0 2017-12-05 22:17:41 2017-11-27 13:42:45 8 33176de67c05eeed870fd49f234387a0 2018-06-04 17:03:57 2018-02-22 09:03:57 102 39104edef5e46d7b8c61848cc95e6d97 2017-10-01 10:11:40 2017-07-12 16:04:41 81 3e43e6105506432c953e165fb2acf44c 2017-12-01 22:37:41 2017-09-18 18:53:15 74 4e1cce07cd5937c69dacac3c8b13d965 2018-07-30 16:04:45 2017-11-25 15:48:03 247 51838d41add414a0b1b989b7d251d9ee 2017-06-04 14:53:58 2017-03-13 18:14:36 83 593cb774409e5239a1946d1c88e0813d 2017-07-05 12:03:14 2017-05-06 15:43:19 60 5b3186d7cf904f2f9369aec26faba4d2 2017-11-24 16:31:04 2017-09-20 17:12:10 65 5bdb6f56a8fb4272b802f504bb6d1287 2018-02-06 12:16:55 2018-02-06 12:16:50 0 64df076fb557552498049bb07ed1cd5f 2018-05-10 10:13:46 2018-04-25 10:52:10 15 6bb535b0906b43e0041916897667aeed 2017-09-17 18:12:09 2017-06-08 22:46:23 101 7305430719d715992b00be82af4a6aa8 2018-04-19 21:00:58 2017-07-12 10:50:31 281 7588c20c457369de8caad958afc1cc06 2018-03-16 15:44:57 2017-01-27 09:33:01 413 76a0491dd70c125840fa259f00dfc351 2018-04-14 12:00:13 2018-01-14 14:19:02 90 7a311d62282fa63be12b02aef2fd21d1 2018-01-30 23:32:03 2017-05-21 08:00:14 254 821e75291b1ad362e614c0ea79fc95a6 2018-07-23 01:03:24 2018-04-24 00:20:19 90 8689b3e15d4b16cfd05ecf597a523453 2018-01-12 16:26:06 2017-03-30 13:21:20 288 894382535eef1ce243ec19088626be0e 2018-03-05 09:38:00 2017-09-20 15:08:28 166 8961b4ca2c5aceb7a78ea72c6e0c840a 2018-06-23 17:45:33 2017-11-27 22:10:49 208 90f323e9f0948ddd96c6f6a8ecc75830 2017-06-05 00:11:24 2017-03-15 22:59:23 82 9aae8213ff9bc04cc3ce48b85f43a173 2018-05-27 18:33:39 2018-05-27 18:14:56 0 a7657330b1c135f3acd420326e335b2c 2017-11-03 20:03:34 2017-05-18 20:51:06 169 abfe742e782fb10f5c824fcb849e5cd1 2017-08-18 14:30:22 2017-08-18 14:30:19 0 af5454198a97379394cacf676e1e96cb 2018-10-03 18:55:29 2018-08-10 10:39:43 54 b64ebaf3d11b7209fe566364cc359a51 2017-07-17 22:44:24 2017-07-17 22:44:21 0 ba77e9b6506636dcbd03e463d4786f24 2017-07-02 20:47:24 2017-04-14 19:35:35 79 ba87a137c5191264841e0be40e53f4ed 2018-02-21 08:39:03 2018-02-21 08:39:02 0 bd86b1862fe796149a4d2af57bd85451 2018-06-07 22:52:43 2018-03-28 20:31:08 71 c37cc6c1a59d81460a3059744f7ada1c 2017-08-29 18:20:51 2017-07-02 22:56:09 58 cecc19ff12c206e6368dd1e9c22a848d 2018-03-19 17:40:34 2017-03-01 17:58:28 383 d02cbb85434c84acabb8e81bbf064d3e 2018-04-05 22:07:30 2017-09-16 17:04:01 201 d3359a56d96666ac0c21bb01e7a61c95 2018-01-12 20:23:42 2017-08-24 22:39:14 141 e4b98eebb8983cade8610c0def59f705 2017-05-02 16:36:02 2017-03-25 09:08:40 38 ec7f1811826ab04a27a92197bc40c888 2017-11-20 11:00:54 2017-11-02 15:17:45 18 f64ec6d8dd29940264cd0bbb5ecade8a 2017-11-19 14:47:50 2017-10-07 06:49:55 43 fe59d5878cd80080edbd29b5a0a4e1cf 2017-08-22 11:50:48 2017-06-07 19:54:10 76 041caba6a63ace5818387698ea85cdb2 2018-05-24 13:50:33 2017-03-15 21:50:14 435 0b18593e033697810a62a987e77f4b8c 2018-03-13 08:07:13 2017-06-02 09:18:44 284 0cc2ee1112a11a1094eff52fa2e87150 2017-10-03 11:54:16 2017-05-15 09:00:01 141 12f5d6e1cbf93dafd9dcc19095df0b3d 2017-01-05 14:23:54 2017-01-05 14:18:03 0 1b6c7548a2a1f9037c1fd3ddfed95f33 2017-12-04 21:11:15 2017-11-13 16:44:41 21 1fbd81e4d0a0cf9125ca038b43533b7f 2018-02-15 21:03:05 2017-05-05 07:48:46 286 2004ba7732339d9be65f2236d8887ae4 2018-05-10 11:23:03 2017-10-03 21:08:38 219 23339103d82a054f9729b0554ce22e8c 2018-06-16 11:58:28 2018-05-30 16:57:26 17 26a6e3e036636ef1d5636f98b66094cc 2018-06-19 12:51:41 2018-01-16 20:56:48 154 31d332d20895c5c0baefe55207a0fead 2018-07-17 01:02:33 2017-05-14 21:56:13 429 34b0cd95480e55c2a701293a2

## Sexta pergunta:  Qual o recebimento anual médio por tipo de pagamento

In [0]:
display(payments)

order_id payment_sequential payment_type payment_installments payment_value b81ef226f3fe1789b1e8b2acac839d17 1 credit_card 8 99.33 a9810da82917af2d9aefd1278f1dcfa0 1 credit_card 1 24.39 25e8ea4e93396b6fa0d3dd708e76c1bd 1 credit_card 1 65.71 ba78997921bbcdc1373bb41e913ab953 1 credit_card 8 107.78 42fdf880ba16b47b59251dd489d4441a 1 credit_card 2 128.45 298fcdf1f73eb413e4d26d01b25bc1cd 1 credit_card 2 96.12 771ee386b001f06208a7419e4fc1bbd7 1 credit_card 1 81.16 3d7239c394a212faae122962df514ac7 1 credit_card 3 51.84 1f78449c87a54faf9e96e88ba1491fa9 1 credit_card 6 341.09 0573b5e23cbd798006520e1d5b4c6714 1 boleto 1 51.95 d88e0d5fa41661ce03cf6cf336527646 1 credit_card 8 188.73 2480f727e869fdeb397244a21b721b67 1 credit_card 1 141.90 616105c9352a9668c38303ad44e056cd 1 credit_card 1 75.78 cf95215a722f3ebf29e6bbab87a29e61 1 credit_card 5 102.66 769214176682788a92801d8907fa1b40 1 credit_card 4 105.28 12e5cfe0e4716b59afb0e0f4a3bd6570 1 credit_card 10 157.45 61059985a6fc0ad64e95d9944caacdad 1 credit_card 1 132.04 79da3f5fe31ad1e454f06f95dc032ad5 1 credit_card 1 98.94 8ac09207f415d55acff302df7d6a895c 1 credit_card 4 244.15 b2349a3f20dfbeef62e7b31baa22f84b 1 credit_card 3 136.71 5a1f6d22f7dfb061ef29216b9af687a1 1 credit_card 4 47.69 4214cda550ece8ee66441f459dc33a8c 1 credit_card 2 170.57 adfbf6c2a620196f9a3ec747491c72b7 1 credit_card 4 67.50 4d680edbaa7d3d9bed69532957368a03 1 credit_card 10 353.09 8cd68144cdb62dc0d60848cf8616d2a4 1 boleto 1 330.66 5cfd514482e22bc992e7693f0e3e8df7 2 voucher 1 45.17 d0a945f85ba1074b60aac97ade7e240e 1 credit_card 2 541.00 c39414c195d0f94c9d9c35e7c6ed4f1a 1 credit_card 2 139.22 5d9c5817e278892b7498d90bfa28ade8 1 credit_card 2 290.16 b69b9260e79a0da00e15f48de1bd2524 1 boleto 1 283.34 f45074ae38f2e01d9b854ec8d40362ff 1 credit_card 1 13.78 81cedc4d2132eb6f512354166e51b187 1 credit_card 1 30.28 595f598849d89203c28d05d0fbf3f92e 1 credit_card 1 26.58 f9d0ec2fa088ac583e1ccd15b6686073 1 credit_card 1 89.68 e647bf617de735448a4ba54f8910393c 1 credit_card 1 65.09 b2bb080b6bc860118a246fd9b6fad6da 1 credit_card 1 173.84 23f10f509600c30cf2852f9dbdf28fc3 1 credit_card 1 103.49 f86f6472fa9f395d8d9a6751ca118afb 1 credit_card 1 64.03 1dcf0c8cd36ffaf57784fbdc90079310 1 credit_card 3 157.15 00d8d65b666158b633f96054d31af43b 1 boleto 1 130.88 cf30fe76d1505192acee1c6dccb15545 1 credit_card 2 47.72 d3e774a185c0b1b2286ffd6c70abe2e6 1 credit_card 8 117.74 32b1d8f3789a57f1f752e20ac7404b4c 1 boleto 1 56.60 c10d412026c4077b8e83acf0fea04eee 1 credit_card 1 266.16 56c3277583e16009c925fdf116df420f 1 boleto 1 31.38 0e0441786430b7cfcd0d91f822ea4c99 1 credit_card 1 121.49 6ffb3f1686bceae3466facf7e02ce3fb 1 credit_card 1 32.00 afef48d3c8a0b1b7c9b7f8f922fb5674 1 credit_card 5 153.41 c0db7d31ace61fc360a3eaa34dd3457c 1 credit_card 5 65.71 d574338f566ca28dd67820f48ec1f1d8 1 credit_card 4 278.22 1807cc736321f14baa58ef39cf6e5989 1 credit_card 4 91.66 e8977f709bbb0367f51b589e6325f991 1 credit_card 1 132.51 2e2c60b99754ae1e4d8b18846cfec9f2 1 credit_card 4 542.66 1ffb3c1929b16d9c1aec1958e11b3e9b 1 boleto 1 166.04 95442deb81a5d91c97c0df96b431634a 1 boleto 1 368.98 10af96a0689260134307879127ac1952 1 credit_card 2 113.20 85eef2d342b0de363c45c1bc324729c5 1 credit_card 3 99.43 aa964845f1de8125410aea8b73e9e1ec 1 credit_card 2 27.35 343348b1e29e9fa9e7b6ab1027f9177d 1 credit_card 4 43.77 ad4098a257676ea4d394fb3bbbf36ca3 1 credit_card 2 68.49 3e0c3cab458e8b3cc8d1d38ecb7e7775 1 credit_card 2 105.53 3ab4eea6776259ae8dfbabaeffece352 1 credit_card 8 387.80 10d9871bed9fb8d0887d3b9022edd1ff 1 boleto 1 84.14 c108072ab31ec90a754129c171577f5f 1 credit_card 4 210.82 fc662bafa52d2ef16078f6f6141009d6 1 boleto 1 90.05 4217849b1ff18a9270fe048eabc4dc45 1 credit_card 1 67.88 795c16acb4e3c30dfa5b6827727ef488 1 credit_card 2 37.58 55e2d723733c45033e71cb4d44690234 1 boleto 1 89.63 947e9c6bfd83a06953c420ef92d3da6e 1 voucher 1 69.46 60e43c5f5ba559d9dd19357ed72cb2f2 1 credit_card 2 78.30 e3e9e3295f4e1512167c232a0aaae8a5 1 voucher 1 50.80 460d57443ffdcaeba240360239747cf7 1 credit_card 1 

In [0]:
orders_with_payment = orders.join(payments, on="order_id", how="left")

display(orders_with_payment)

order_id customer_id order_status order_purchase_timestamp order_approved_at order_delivered_carrier_date order_delivered_customer_date order_estimated_delivery_date payment_sequential payment_type payment_installments payment_value e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 2 voucher 1 18.59 e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 3 voucher 1 2.00 e481f51cbdc54678b7cc49136f2d6af7 9ef432eb6251297304e76186b10a928d delivered 2017-10-02 10:56:33 2017-10-02 11:07:15 2017-10-04 19:55:00 2017-10-10 21:25:13 2017-10-18 00:00:00 1 credit_card 1 18.12 53cdb2fc8bc7dce0b6741e2150273451 b0830fb4747a6c6d20dea0b8c802d7ef delivered 2018-07-24 20:41:37 2018-07-26 03:24:27 2018-07-26 14:31:00 2018-08-07 15:27:45 2018-08-13 00:00:00 1 boleto 1 141.46 47770eb9100c2d0c44946d9cf07ec65d 41ce2a54c0b03bf3443c3d931a367089 delivered 2018-08-08 08:38:49 2018-08-08 08:55:23 2018-08-08 13:50:00 2018-08-17 18:06:29 2018-09-04 00:00:00 1 credit_card 3 179.12 949d5b44dbf5de918fe9c16f97b45f8a f88197465ea7920adcdbec7375364d82 delivered 2017-11-18 19:28:06 2017-11-18 19:45:59 2017-11-22 13:39:59 2017-12-02 00:28:42 2017-12-15 00:00:00 1 credit_card 1 72.20 ad21c59c0840e6cb83a9ceb5573f8159 8ab97904e6daea8866dbdbc4fb7aad2c delivered 2018-02-13 21:18:39 2018-02-13 22:20:29 2018-02-14 19:46:34 2018-02-16 18:17:02 2018-02-26 00:00:00 1 credit_card 1 28.62 a4591c265e18cb1dcee52889e2d8acc3 503740e9ca751ccdda7ba28e9ab8f608 delivered 2017-07-09 21:57:05 2017-07-09 22:10:13 2017-07-11 14:58:04 2017-07-26 10:57:55 2017-08-01 00:00:00 1 credit_card 6 175.26 136cce7faa42fdb2cefd53fdc79a6098 ed0271e0b7da060a393796590e7b737a invoiced 2017-04-11 12:22:08 2017-04-13 13:25:17 null null 2017-05-09 00:00:00 1 credit_card 1 65.95 6514b8ad8028c9f2cc2374ded245783f 9bdf08b4b3b52b5526ff42d37d47f222 delivered 2017-05-16 13:10:30 2017-05-16 13:22:11 2017-05-22 10:07:46 2017-05-26 12:55:51 2017-06-07 00:00:00 1 credit_card 3 75.16 76c6e866289321a7c93b82b54852dc33 f54a9f0e6b351c431402b8461ea51999 delivered 2017-01-23 18:29:09 2017-01-25 02:50:47 2017-01-26 14:16:31 2017-02-02 14:08:10 2017-03-06 00:00:00 1 boleto 1 35.95 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 1 credit_card 1 8.34 e69bfb5eb88e0ed6a785585b27e16dbf 31ad1d1b63eb9962463f764d4e6e0c9d delivered 2017-07-29 11:55:02 2017-07-29 12:05:32 2017-08-10 19:45:24 2017-08-16 17:14:30 2017-08-23 00:00:00 2 voucher 1 161.42 e6ce16cb79ec1d90b1da9085a6118aeb 494dded5b201313c64ed7f100595b95c delivered 2017-05-16 19:41:10 2017-05-16 19:50:18 2017-05-18 11:40:40 2017-05-29 11:18:31 2017-06-07 00:00:00 1 credit_card 1 259.06 34513ce0c4fab462a55830c0989c7edb 7711cf624183d843aafe81855097bc37 delivered 2017-07-13 19:58:11 2017-07-13 20:10:08 2017-07-14 18:43:29 2017-07-19 14:04:48 2017-08-08 00:00:00 1 credit_card 1 114.13 82566a660a982b15fb86e904c8d32918 d3e3b74c766bc6214e0c830b17ee2341 delivered 2018-06-07 10:06:19 2018-06-09 03:13:12 2018-06-11 13:29:00 2018-06-19 12:05:52 2018-07-18 00:00:00 1 boleto 1 50.13 5ff96c15d0b717ac6ad1f3d77225a350 19402a48fe860416adf93348aba37740 delivered 2018-07-25 17:44:10 2018-07-25 17:55:14 2018-07-26 13:16:00 2018-07-30 15:52:25 2018-08-08 00:00:00 1 credit_card 3 32.70 432aaf21d85167c2c86ec9448c4e42cc 3df704f53d3f1d4818840b34ec672a9f delivered 2018-03-01 14:14:28 2018-03-01 15:10:47 2018-03-02 21:09:20 2018-03-12 23:36:26 2018-03-21 00:00:00 1 credit_card 1 54.36 dcb36b511fcac050b97cd5c05de84dc3 3b6828a50ffe546942b7a473d70ac0fc delivered 2018-06-07 19:03:12 2018-06-12 23:31:02 2018-06-11 14:54:00 2018-06-21 15:34:32 2018-07-04 00:00:00 1 credit_card 10 146.45 403b97836b0c04a622354cf531062e5f 738b086814c6fcc74b8cc583

In [0]:
answer_6 = (orders_with_payment
            .groupby(F.year(F.col("order_purchase_timestamp")), "payment_type")
            .agg(F.sum(F.col("payment_value"))
                 .alias("sum_payment_type"))
            .groupby("payment_type")
            .agg(F.avg(F.col("sum_payment_type"))
                 .alias("mean_total_payment_received_per_year"))
           )

display(answer_6)

payment_type mean_total_payment_received_per_year null null boleto 956453.7566666681 not_defined 0.0 credit_card 4180694.730000008 voucher 126478.95666666667 debit_card 72663.26333333337

#### Por fim, vamos falar de como criar funções customizadas para operar sobre nossos dados

Essas funções são chamadas de *user defined functions* (UDF) e são úteis para criarmos funções personalizadas, pois temos todo o arsenal da linguagem *Python* ao nosso dispor.

Mas sempre usem com cautela, pois essas funções são vistas como "caixas-pretas" pelo *Spark*, ou seja, ele não consegue aplicar o processo de otimização de queries quando encontra esse tipo de operação.

Além disso, esse tipo de função gera um *overhead* excessivo, pois os dados precisam ser serializados para tanto na ida (para comunicação entre o *Python* e a JVM) quanto na volta (comunicação entre a JVM e o *Python*).

Esse é um assunto interessante, que engloba necessita de mais conhecimento do funcionamento interno do Spark para completo entendimento dos contras.

O que vocês devem ter em mente é:

## Somente usem UDF's quando o que necessitarem não estiver implementado nativamente!

In [0]:
@F.udf(returnType=T.FloatType())
def multiply_by_two(data):
  return 2*data

In [0]:
#Observem a conversão no tipo do dado (algumas pessoas realizam essa conversam passando a string "float" para o método cast)
display(payments.withColumn("test", multiply_by_two(F.col("payment_value").cast(T.FloatType()))))

order_id payment_sequential payment_type payment_installments payment_value test b81ef226f3fe1789b1e8b2acac839d17 1 credit_card 8 99.33 198.66 a9810da82917af2d9aefd1278f1dcfa0 1 credit_card 1 24.39 48.78 25e8ea4e93396b6fa0d3dd708e76c1bd 1 credit_card 1 65.71 131.42 ba78997921bbcdc1373bb41e913ab953 1 credit_card 8 107.78 215.56 42fdf880ba16b47b59251dd489d4441a 1 credit_card 2 128.45 256.9 298fcdf1f73eb413e4d26d01b25bc1cd 1 credit_card 2 96.12 192.24 771ee386b001f06208a7419e4fc1bbd7 1 credit_card 1 81.16 162.32 3d7239c394a212faae122962df514ac7 1 credit_card 3 51.84 103.68 1f78449c87a54faf9e96e88ba1491fa9 1 credit_card 6 341.09 682.18 0573b5e23cbd798006520e1d5b4c6714 1 boleto 1 51.95 103.9 d88e0d5fa41661ce03cf6cf336527646 1 credit_card 8 188.73 377.46 2480f727e869fdeb397244a21b721b67 1 credit_card 1 141.90 283.8 616105c9352a9668c38303ad44e056cd 1 credit_card 1 75.78 151.56 cf95215a722f3ebf29e6bbab87a29e61 1 credit_card 5 102.66 205.32 769214176682788a92801d8907fa1b40 1 credit_card 4 105.28 210.56 12e5cfe0e4716b59afb0e0f4a3bd6570 1 credit_card 10 157.45 314.9 61059985a6fc0ad64e95d9944caacdad 1 credit_card 1 132.04 264.08 79da3f5fe31ad1e454f06f95dc032ad5 1 credit_card 1 98.94 197.88 8ac09207f415d55acff302df7d6a895c 1 credit_card 4 244.15 488.3 b2349a3f20dfbeef62e7b31baa22f84b 1 credit_card 3 136.71 273.42 5a1f6d22f7dfb061ef29216b9af687a1 1 credit_card 4 47.69 95.38 4214cda550ece8ee66441f459dc33a8c 1 credit_card 2 170.57 341.14 adfbf6c2a620196f9a3ec747491c72b7 1 credit_card 4 67.50 135.0 4d680edbaa7d3d9bed69532957368a03 1 credit_card 10 353.09 706.18 8cd68144cdb62dc0d60848cf8616d2a4 1 boleto 1 330.66 661.32 5cfd514482e22bc992e7693f0e3e8df7 2 voucher 1 45.17 90.34 d0a945f85ba1074b60aac97ade7e240e 1 credit_card 2 541.00 1082.0 c39414c195d0f94c9d9c35e7c6ed4f1a 1 credit_card 2 139.22 278.44 5d9c5817e278892b7498d90bfa28ade8 1 credit_card 2 290.16 580.32 b69b9260e79a0da00e15f48de1bd2524 1 boleto 1 283.34 566.68 f45074ae38f2e01d9b854ec8d40362ff 1 credit_card 1 13.78 27.56 81cedc4d2132eb6f512354166e51b187 1 credit_card 1 30.28 60.56 595f598849d89203c28d05d0fbf3f92e 1 credit_card 1 26.58 53.16 f9d0ec2fa088ac583e1ccd15b6686073 1 credit_card 1 89.68 179.36 e647bf617de735448a4ba54f8910393c 1 credit_card 1 65.09 130.18 b2bb080b6bc860118a246fd9b6fad6da 1 credit_card 1 173.84 347.68 23f10f509600c30cf2852f9dbdf28fc3 1 credit_card 1 103.49 206.98 f86f6472fa9f395d8d9a6751ca118afb 1 credit_card 1 64.03 128.06 1dcf0c8cd36ffaf57784fbdc90079310 1 credit_card 3 157.15 314.3 00d8d65b666158b633f96054d31af43b 1 boleto 1 130.88 261.76 cf30fe76d1505192acee1c6dccb15545 1 credit_card 2 47.72 95.44 d3e774a185c0b1b2286ffd6c70abe2e6 1 credit_card 8 117.74 235.48 32b1d8f3789a57f1f752e20ac7404b4c 1 boleto 1 56.60 113.2 c10d412026c4077b8e83acf0fea04eee 1 credit_card 1 266.16 532.32 56c3277583e16009c925fdf116df420f 1 boleto 1 31.38 62.76 0e0441786430b7cfcd0d91f822ea4c99 1 credit_card 1 121.49 242.98 6ffb3f1686bceae3466facf7e02ce3fb 1 credit_card 1 32.00 64.0 afef48d3c8a0b1b7c9b7f8f922fb5674 1 credit_card 5 153.41 306.82 c0db7d31ace61fc360a3eaa34dd3457c 1 credit_card 5 65.71 131.42 d574338f566ca28dd67820f48ec1f1d8 1 credit_card 4 278.22 556.44 1807cc736321f14baa58ef39cf6e5989 1 credit_card 4 91.66 183.32 e8977f709bbb0367f51b589e6325f991 1 credit_card 1 132.51 265.02 2e2c60b99754ae1e4d8b18846cfec9f2 1 credit_card 4 542.66 1085.32 1ffb3c1929b16d9c1aec1958e11b3e9b 1 boleto 1 166.04 332.08 95442deb81a5d91c97c0df96b431634a 1 boleto 1 368.98 737.96 10af96a0689260134307879127ac1952 1 credit_card 2 113.20 226.4 85eef2d342b0de363c45c1bc324729c5 1 credit_card 3 99.43 198.86 aa964845f1de8125410aea8b73e9e1ec 1 credit_card 2 27.35 54.7 343348b1e29e9fa9e7b6ab1027f9177d 1 credit_card 4 43.77 87.54 ad4098a257676ea4d394fb3bbbf36ca3 1 credit_card 2 68.49 136.98 3e0c3cab458e8b3cc8d1d38ecb7e7775 1 credit_card 2 105.53 211.06 3ab4eea6776259ae8dfbabaeffece352 1 credit_card 8 387.80 775.6 10d9871bed9fb8d0887d3b9022edd1ff 1 boleto 1 84.14 168.28 c108072ab31ec90a754129c171577f5f 1 credit_card 4

Também podemos escrever a UDF como uma função lambda:

```
multiply_by_two = F.udf(lambda x: 2*x, returnType=T.FloatType())
```